In [1]:
#ngboost and modelling libraries
from ngboost import NGBClassifier
from ngboost.distns import Bernoulli
from sklearn.tree import DecisionTreeRegressor
from sklearn.metrics import roc_auc_score, roc_curve, classification_report
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
from imblearn.over_sampling import SMOTE
from collections import Counter

#data manipulation libraries
import pandas as pd
import numpy as np

from plotly.offline import init_notebook_mode
init_notebook_mode(connected=True)

#ignore warnings
import warnings
warnings.filterwarnings('ignore')

#import functions and constants
from utils import (register_imputation, preprocess_df, 
                    scaling_values_df, clean_outliers, get_sample_weights, 
                  process_unit_cost, cost_score, generate_y_pred_with_custom_threshold, 
                  calculate_cost_score_with_learning, calculate_learning_cost, process_learning_unit_cost,)
from plot_utils import (correlation_heatmap, visualize_permutation_feature_importances, 
                        plot_target_balance, plot_trace_line, plot_scatter_matrix, 
                        plot_feature_importances, visualize_roc_curve, color_negative_red, )

from constants import cols, cols_with_missing_indicators

In [2]:
SEED=2020

## READING DATAFRAME

In [3]:
df = pd.read_csv("./data/cs-training.csv", usecols =cols)

In [4]:
df.head()

SeriousDlqin2yrs  RevolvingUtilizationOfUnsecuredLines  age  \
0                 1                              0.766127   45   
1                 0                              0.957151   40   
2                 0                              0.658180   38   
3                 0                              0.233810   30   
4                 0                              0.907239   49   

   NumberOfTime30-59DaysPastDueNotWorse  DebtRatio  MonthlyIncome  \
0                                     2   0.802982         9120.0   
1                                     0   0.121876         2600.0   
2                                     1   0.085113         3042.0   
3                                     0   0.036050         3300.0   
4                                     1   0.024926        63588.0   

   NumberOfOpenCreditLinesAndLoans  NumberOfTimes90DaysLate  \
0                               13                        0   
1                                4                        0   
2                                2                        1   
3                                5                        0   
4                                7                        0   

   NumberRealEstateLoansOrLines  NumberOfTime60-89DaysPastDueNotWorse  \
0                             6                                     0   
1                             0                                     0   
2                             0                                     0   
3                             0                                     0   
4                             1                                     0   

   NumberOfDependents  
0                 2.0  
1                 1.0  
2                 0.0  
3                 0.0  
4                 0.0

In [5]:
len(df)

150000

## FEATURE ENGINEERING

In [6]:

def preprocess_extra(df):
    """
    Extra cleanup process of some outliers.
    """
    df.loc[
        (df["RevolvingUtilizationOfUnsecuredLines"] > 1),
        "RevolvingUtilizationOfUnsecuredLines",
    ] = 0
    df.loc[(df["DebtRatio"] > 10), "DebtRatio"] = 0
    df.loc[(df["age"] < 18), "age"] = 0

In [7]:
from sklearn.neighbors import LocalOutlierFactor
def clean_outliers(df, flag_filter=False):
    """ 
    Register imputations, identify outliers with LOF and clean them. Also it process an extra function to clean some outliers.

    Args:
        - df (DataFrame Object): dataframe to be processed
        - flag_filter (boolean): Flag that indicates if the process requres an extra cleanup of outliers.

    Returns dataframe without outliers
    """
    #df = preprocess_df(df.copy())
    df = register_imputation(df.copy())
    local_outlier_factor = LocalOutlierFactor(contamination=0.1)
    is_outlier = local_outlier_factor.fit_predict(df[cols[1:]]) == -1
    data_outlier_excluded = df.loc[~is_outlier, :]
    if flag_filter:
        preprocess_extra(data_outlier_excluded)
    return data_outlier_excluded

In [8]:
df = clean_outliers(df.copy(), True)

In [9]:
cols_f = [c for c in df.columns if 'dummy' not in c.lower()]

df_cleaned=df.copy()[cols_f].reset_index(drop=True)

In [10]:
del df
df = df_cleaned.copy()
df

SeriousDlqin2yrs  RevolvingUtilizationOfUnsecuredLines  age  \
0                      1                              0.766127   45   
1                      0                              0.957151   40   
2                      0                              0.658180   38   
3                      0                              0.233810   30   
4                      0                              0.907239   49   
...                  ...                                   ...  ...   
134995                 0                              0.040674   74   
134996                 0                              0.299745   44   
134997                 0                              0.246044   58   
134998                 0                              0.000000   30   
134999                 0                              0.850283   64   

        NumberOfTime30-59DaysPastDueNotWorse  DebtRatio  MonthlyIncome  \
0                                          2   0.802982         9120.0   
1                                          0   0.121876         2600.0   
2                                          1   0.085113         3042.0   
3                                          0   0.036050         3300.0   
4                                          1   0.024926        63588.0   
...                                      ...        ...            ...   
134995                                     0   0.225131         2100.0   
134996                                     0   0.716562         5584.0   
134997                                     0   0.000000            0.0   
134998                                     0   0.000000         5716.0   
134999                                     0   0.249908         8158.0   

        NumberOfOpenCreditLinesAndLoans  NumberOfTimes90DaysLate  \
0                                    13                        0   
1                                     4                        0   
2                                     2                        1   
3                                     5                        0   
4                                     7                        0   
...                                 ...                      ...   
134995                                4                        0   
134996                                4                        0   
134997                               18                        0   
134998                                4                        0   
134999                                8                        0   

        NumberRealEstateLoansOrLines  NumberOfTime60-89DaysPastDueNotWorse  \
0                                  6                                     0   
1                                  0                                     0   
2                                  0                                     0   
3                                  0                                     0   
4                                  1                                     0   
...                              ...                                   ...   
134995                             1                                     0   
134996                             1                                     0   
134997                             1                                     0   
134998                             0                                     0   
134999                             2                                     0   

        NumberOfDependents  
0                      2.0  
1                      1.0  
2                      0.0  
3                      0.0  
4                      0.0  
...                    ...  
134995                 0.0  
134996                 2.0  
134997                 0.0  
134998                 0.0  
134999                 0.0  

[135000 rows x 11 columns]

In [11]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 135000 entries, 0 to 134999
Data columns (total 11 columns):
SeriousDlqin2yrs                        135000 non-null int64
RevolvingUtilizationOfUnsecuredLines    135000 non-null float64
age                                     135000 non-null int64
NumberOfTime30-59DaysPastDueNotWorse    135000 non-null int64
DebtRatio                               135000 non-null float64
MonthlyIncome                           135000 non-null float64
NumberOfOpenCreditLinesAndLoans         135000 non-null int64
NumberOfTimes90DaysLate                 135000 non-null int64
NumberRealEstateLoansOrLines            135000 non-null int64
NumberOfTime60-89DaysPastDueNotWorse    135000 non-null int64
NumberOfDependents                      135000 non-null float64
dtypes: float64(4), int64(7)
memory usage: 11.3 MB


In [12]:
print(df.isnull().sum())

SeriousDlqin2yrs                        0
RevolvingUtilizationOfUnsecuredLines    0
age                                     0
NumberOfTime30-59DaysPastDueNotWorse    0
DebtRatio                               0
MonthlyIncome                           0
NumberOfOpenCreditLinesAndLoans         0
NumberOfTimes90DaysLate                 0
NumberRealEstateLoansOrLines            0
NumberOfTime60-89DaysPastDueNotWorse    0
NumberOfDependents                      0
dtype: int64


In [13]:
df.describe()

SeriousDlqin2yrs  RevolvingUtilizationOfUnsecuredLines            age  \
count     135000.000000                         135000.000000  135000.000000   
mean           0.060726                              0.294336      52.143319   
std            0.238828                              0.335301      14.336519   
min            0.000000                              0.000000      21.000000   
25%            0.000000                              0.024932      41.000000   
50%            0.000000                              0.132987      52.000000   
75%            0.000000                              0.499763      62.000000   
max            1.000000                              1.000000      99.000000   

       NumberOfTime30-59DaysPastDueNotWorse      DebtRatio  MonthlyIncome  \
count                         135000.000000  135000.000000  135000.000000   
mean                               0.280696       0.328392    5089.181052   
std                                2.515978       0.673520    5747.339847   
min                                0.000000       0.000000       0.000000   
25%                                0.000000       0.003842    1251.750000   
50%                                0.000000       0.214178    4250.000000   
75%                                0.000000       0.412272    7200.000000   
max                               98.000000      10.000000  151855.000000   

       NumberOfOpenCreditLinesAndLoans  NumberOfTimes90DaysLate  \
count                    135000.000000            135000.000000   
mean                          8.098289                 0.134000   
std                           4.526645                 2.472258   
min                           0.000000                 0.000000   
25%                           5.000000                 0.000000   
50%                           7.000000                 0.000000   
75%                          11.000000                 0.000000   
max                          57.000000                98.000000   

       NumberRealEstateLoansOrLines  NumberOfTime60-89DaysPastDueNotWorse  \
count                 135000.000000                         135000.000000   
mean                       0.996363                              0.117170   
std                        1.045003                              2.459597   
min                        0.000000                              0.000000   
25%                        0.000000                              0.000000   
50%                        1.000000                              0.000000   
75%                        2.000000                              0.000000   
max                       32.000000                             98.000000   

       NumberOfDependents  
count       135000.000000  
mean             0.724215  
std              1.084068  
min              0.000000  
25%              0.000000  
50%              0.000000  
75%              1.000000  
max             10.000000

## NGBOOST MODEL

In [14]:
import random
random.seed(2019)
list_of_ids_train=random.sample(range(0,len(df)), int(len(df) * 0.2))

In [15]:
df['NumberRealEstateLoansOrLines'] = df['NumberRealEstateLoansOrLines'].astype(float)
df['NumberOfOpenCreditLinesAndLoans'] = df['NumberOfOpenCreditLinesAndLoans'].astype(float)

In [16]:
for idx in list_of_ids_train:
    for col in ['MonthlyIncome', 'NumberRealEstateLoansOrLines', 'NumberOfOpenCreditLinesAndLoans']: #en el segundo lugar estaba dummy_MonthlyIncome
        df.at[idx, col] = np.nan

In [17]:
def register_imputation(df):
    """
    Register imputations of certain df
    Args:
        - df (DataFrame): Dataframe to be computed
    Return df with filled values and booleans that indicate if each row was changed
    """
    for c in cols[1:]:
        # df[f"{c}_amputado"] = df[f"{c}"].fillna(0)
        df[f"{c}_imputed"] = df[f"{c}"].fillna(0)
        df[f"dummy_{c}"] = (df[f"{c}"] != df[f"{c}_imputed"]).astype(int)
        del df[f"{c}"]
        df.columns = df.columns.str.replace(f"{c}_imputed", f"{c}")
    return df


In [18]:
df = register_imputation(df.copy())

In [20]:
df.isnull().any().any()

False

In [20]:
X = df.drop(columns=['SeriousDlqin2yrs']).values
y = df.SeriousDlqin2yrs.values

In [21]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [22]:
df

SeriousDlqin2yrs  RevolvingUtilizationOfUnsecuredLines  \
0                      1                              0.766127   
1                      0                              0.957151   
2                      0                              0.658180   
3                      0                              0.233810   
4                      0                              0.907239   
...                  ...                                   ...   
134995                 0                              0.040674   
134996                 0                              0.299745   
134997                 0                              0.246044   
134998                 0                              0.000000   
134999                 0                              0.850283   

        dummy_RevolvingUtilizationOfUnsecuredLines  age  dummy_age  \
0                                                0   45          0   
1                                                0   40          0   
2                                                0   38          0   
3                                                0   30          0   
4                                                0   49          0   
...                                            ...  ...        ...   
134995                                           0   74          0   
134996                                           0   44          0   
134997                                           0   58          0   
134998                                           0   30          0   
134999                                           0   64          0   

        NumberOfTime30-59DaysPastDueNotWorse  \
0                                          2   
1                                          0   
2                                          1   
3                                          0   
4                                          1   
...                                      ...   
134995                                     0   
134996                                     0   
134997                                     0   
134998                                     0   
134999                                     0   

        dummy_NumberOfTime30-59DaysPastDueNotWorse  DebtRatio  \
0                                                0   0.802982   
1                                                0   0.121876   
2                                                0   0.085113   
3                                                0   0.036050   
4                                                0   0.024926   
...                                            ...        ...   
134995                                           0   0.225131   
134996                                           0   0.716562   
134997                                           0   0.000000   
134998                                           0   0.000000   
134999                                           0   0.249908   

        dummy_DebtRatio  MonthlyIncome  ...  NumberOfOpenCreditLinesAndLoans  \
0                     0         9120.0  ...                             13.0   
1                     0         2600.0  ...                              4.0   
2                     0         3042.0  ...                              2.0   
3                     0         3300.0  ...                              5.0   
4                     0        63588.0  ...                              7.0   
...                 ...            ...  ...                              ...   
134995                0            0.0  ...                              0.0   
134996                0         5584.0  ...                              4.0   
134997                0            0.0  ...                             18.0   
134998                0         5716.0  ...                              4.0   
134999                0            0.0  ...                              0.0   

        dummy_NumberOfOpenCreditLinesAndLoans  NumberOf

In [23]:
nm_common =SMOTE(random_state=2019)
X_train_resampled, y_train_resampled = nm_common.fit_sample(X_train, y_train)
print("Resampled dataset shape {}".format(Counter(y_train_resampled)))

Resampled dataset shape Counter({0: 101492, 1: 101492})


In [24]:
#base0 = DecisionTreeRegressor(criterion="friedman_mse", max_depth=4)
from utils import check_counts
base1 = DecisionTreeRegressor(criterion="friedman_mse", max_depth=4, random_state = SEED)
base2 = DecisionTreeRegressor(criterion="friedman_mse", max_depth=8, random_state = SEED)
base3 = DecisionTreeRegressor(criterion="friedman_mse", max_depth=10, random_state = SEED)
base4 = DecisionTreeRegressor(criterion="friedman_mse", max_depth=12, random_state = SEED)

In [26]:
#FIX MEEEEEEEEEEE: REFACTOR PLZZ !!! second model learning_cost
df_collector = pd.DataFrame(columns=  ["hyperparams", "estimators", 
                                       "learning_rate", "max_depth", "threshold", "count_zero", "count_one",
                                       "cost", 
                                       "train_auc", "test_auc"])
df_collector['hyperparams'] = df_collector['hyperparams'].astype('object')
k = 1131
for estimator in [150, 200, 250,300,350]:
    for lr in [0.01]:
        for baset in [base1,base2,base3,base4]:
            ngb_clf = NGBClassifier(Dist=Bernoulli,
                                      verbose=True, Base=baset, n_estimators = estimator, random_state=SEED,
                                    learning_rate = lr, verbose_eval = 0
                                     )
            print(ngb_clf)
            ngb_clf.fit(X_train_resampled, y_train_resampled, sample_weight= get_sample_weights(y_train, y_train_resampled))
            #en el primer iteraba el threashold desde 0.1 a 0.9 obviamente cuanto mas menor me daba peor.. entonces itero
            #solamente d esde 0.70 a 0.95
            for threshold in list(np.arange(0.20, 0.35, 0.05)):
                count_zero, count_one = check_counts(ngb_clf, X_test, threshold)
                if (count_zero < 3000):
                    pass
                else:
                    if True:
                        df_aux = pd.DataFrame(X_test, columns=cols_with_missing_indicators)
                        df_aux['predicted'] = generate_y_pred_with_custom_threshold(ngb_clf, X_test, threshold)
                        df_aux['real'] = list(y_test)
                        df_aux['LoanPrincipal'] = df_aux.MonthlyIncome * 2
                        cost = cost_score(df_aux.LoanPrincipal, df_aux.predicted, df_aux.real)
                        if True:
                            df_collector.ix[str(k),'hyperparams'] = ngb_clf
                            df_collector.ix[str(k),'estimators'] = estimator
                            df_collector.ix[str(k),'learning_rate'] = lr
                            df_collector.ix[str(k),'max_depth'] = baset.max_depth
                            threshold = round(threshold,2)
                            print("k: "+str(k))
                            print(threshold)
                            print("cost "+str(cost))
                            print("th "+str(threshold))
                            df_collector.ix[str(k),'threshold'] = threshold
                            count_zero, count_one = check_counts(ngb_clf, X_test, threshold)
                            df_collector.ix[str(k),'count_zero'] = count_zero
                            df_collector.ix[str(k),'count_one'] = count_one
                            df_collector.ix[str(k),'cost'] = cost
                            # predict probabilities
                            train_probs = ngb_clf.predict_proba(X_train)
                            test_probs = ngb_clf.predict_proba(X_test)
                            # keep probabilities for the positive outcome only
                            train_probs = train_probs[:, 1]
                            test_probs = test_probs[:, 1]
                            # calculate scores
                            train_auc = roc_auc_score(y_train, train_probs)
                            test_auc = roc_auc_score(y_test, test_probs)
                            df_collector.ix[str(k),'train_auc'] = train_auc
                            df_collector.ix[str(k),'test_auc'] = test_auc
                            k+=1
                            print("sumando k")
                            print("---------------------------------")
            del ngb_clf
df_collector['diff_auc'] = df_collector['train_auc'] - df_collector['test_auc']

NGBClassifier(Base=DecisionTreeRegressor(ccp_alpha=0.0,
                                         criterion='friedman_mse', max_depth=4,
                                         max_features=None, max_leaf_nodes=None,
                                         min_impurity_decrease=0.0,
                                         min_impurity_split=None,
                                         min_samples_leaf=1,
                                         min_samples_split=2,
                                         min_weight_fraction_leaf=0.0,
                                         presort='deprecated',
                                         random_state=2020, splitter='best'),
              Dist=<class 'ngboost.distns.categorical.k_categorical.<locals>.Categorical'>,
              Score=<class 'ngboost.scores.LogScore'>, col_sample=1.0,
              learning_rate=0.01, minibatch_frac=1.0, n_estimators=150,
              natural_gradient=True,
              random_state=RandomState(MT1

count_zero 7656
count_one 19344
k: 1143
0.2
cost 2021797.9199999913
th 0.2
sumando k
---------------------------------
count_zero 8924
count_one 18076
k: 1144
0.25
cost 2130654.1399999936
th 0.25
sumando k
---------------------------------
count_zero 10105
count_one 16895
k: 1145
0.3
cost 2351377.619999994
th 0.3
sumando k
---------------------------------
NGBClassifier(Base=DecisionTreeRegressor(ccp_alpha=0.0,
                                         criterion='friedman_mse', max_depth=12,
                                         max_features=None, max_leaf_nodes=None,
                                         min_impurity_decrease=0.0,
                                         min_impurity_split=None,
                                         min_samples_leaf=1,
                                         min_samples_split=2,
                                         min_weight_fraction_leaf=0.0,
                                         presort='deprecated',
                                

NGBClassifier(Base=DecisionTreeRegressor(ccp_alpha=0.0,
                                         criterion='friedman_mse', max_depth=8,
                                         max_features=None, max_leaf_nodes=None,
                                         min_impurity_decrease=0.0,
                                         min_impurity_split=None,
                                         min_samples_leaf=1,
                                         min_samples_split=2,
                                         min_weight_fraction_leaf=0.0,
                                         presort='deprecated',
                                         random_state=2020, splitter='best'),
              Dist=<class 'ngboost.distns.categorical.k_categorical.<locals>.Categorical'>,
              Score=<class 'ngboost.scores.LogScore'>, col_sample=1.0,
              learning_rate=0.01, minibatch_frac=1.0, n_estimators=300,
              natural_gradient=True,
              random_state=RandomState(MT1

k: 1172
0.3
cost 2390016.859999995
th 0.3
sumando k
---------------------------------
NGBClassifier(Base=DecisionTreeRegressor(ccp_alpha=0.0,
                                         criterion='friedman_mse', max_depth=12,
                                         max_features=None, max_leaf_nodes=None,
                                         min_impurity_decrease=0.0,
                                         min_impurity_split=None,
                                         min_samples_leaf=1,
                                         min_samples_split=2,
                                         min_weight_fraction_leaf=0.0,
                                         presort='deprecated',
                                         random_state=2020, splitter='best'),
              Dist=<class 'ngboost.distns.categorical.k_categorical.<locals>.Categorical'>,
              Score=<class 'ngboost.scores.LogScore'>, col_sample=1.0,
              learning_rate=0.01, minibatch_frac=1.0, n_estimato

In [29]:
df_results = df_collector.reset_index(drop=True)

In [31]:
df_results.sort_values("cost").to_csv("resultados_primera_parte_segundo_exp_a_rellenar.csv", index=False)

In [24]:
from plot_utils import visualize_roc_curve
visualize_roc_curve(ngb_clf, X_train, y_train, X_test, y_test)

TRAIN: ROC AUC=0.837
TEST: ROC AUC=0.815


In [25]:
df_aux = pd.DataFrame(X_test, columns=cols_with_missing_indicators)
df_aux['predicted'] = generate_y_pred_with_custom_threshold(ngb_clf, X_test, 0.2)
df_aux['real'] = list(y_test)
df_aux['LoanPrincipal'] = df_aux.MonthlyIncome * 2
cost_score(df_aux.LoanPrincipal, df_aux.predicted, df_aux.real)

count_zero 5108
count_one 21892


1858635.87999999

In [26]:
ngb_clf = NGBClassifier(Base=DecisionTreeRegressor(ccp_alpha=0.0,
                                         criterion='friedman_mse', max_depth=8,
                                         max_features=None, max_leaf_nodes=None,
                                         min_impurity_decrease=0.0,
                                         min_impurity_split=None,
                                         min_samples_leaf=1,
                                         min_samples_split=2,
                                         min_weight_fraction_leaf=0.0,
                                         presort='deprecated',
                                         random_state=2019, splitter='best'),
             col_sample=1.0,
              learning_rate=0.01, minibatch_frac=1.0, n_estimators=350,
              natural_gradient=True, tol=0.0001,
              verbose=True, verbose_eval=0)
ngb_clf.fit(X_train_resampled, y_train_resampled, sample_weight= get_sample_weights(y_train, y_train_resampled))

NGBClassifier(Base=DecisionTreeRegressor(ccp_alpha=0.0,
                                         criterion='friedman_mse', max_depth=8,
                                         max_features=None, max_leaf_nodes=None,
                                         min_impurity_decrease=0.0,
                                         min_impurity_split=None,
                                         min_samples_leaf=1,
                                         min_samples_split=2,
                                         min_weight_fraction_leaf=0.0,
                                         presort='deprecated',
                                         random_state=2019, splitter='best'),
              Dist=<class 'ngboost.distns.categorical.k_categorical.<locals>.Categorical'>,
              Score=<class 'ngboost.scores.LogScore'>, col_sample=1.0,
              learning_rate=0.01, minibatch_frac=1.0, n_estimators=350,
              natural_gradient=True,
              random_state=RandomState(MT1

In [ ]:
from plot_utils import visualize_roc_curve
visualize_roc_curve(ngb_clf, X_train, y_train, X_test, y_test)

In [ ]:
df_aux = pd.DataFrame(X_test, columns=cols_with_missing_indicators)
df_aux['predicted'] = generate_y_pred_with_custom_threshold(ngb_clf, X_test, 0.2)
df_aux['real'] = list(y_test)
df_aux['LoanPrincipal'] = df_aux.MonthlyIncome * 2
cost_score(df_aux.LoanPrincipal, df_aux.predicted, df_aux.real)

In [203]:
ngb_clf = NGBClassifier(Base=DecisionTreeRegressor(ccp_alpha=0.0,
                                         criterion='friedman_mse', max_depth=8,
                                         max_features=None, max_leaf_nodes=None,
                                         min_impurity_decrease=0.0,
                                         min_impurity_split=None,
                                         min_samples_leaf=1,
                                         min_samples_split=2,
                                         min_weight_fraction_leaf=0.0,
                                         presort='deprecated',
                                         random_state=None, splitter='best'),
             col_sample=1.0,
              learning_rate=0.01, minibatch_frac=1.0, n_estimators=100,
              natural_gradient=True, tol=0.0001,
              verbose=True, verbose_eval=0)
ngb_clf.fit(X_train_resampled, y_train_resampled, sample_weight= get_sample_weights(y_train, y_train_resampled))

NGBClassifier(Base=DecisionTreeRegressor(ccp_alpha=0.0,
                                         criterion='friedman_mse', max_depth=8,
                                         max_features=None, max_leaf_nodes=None,
                                         min_impurity_decrease=0.0,
                                         min_impurity_split=None,
                                         min_samples_leaf=1,
                                         min_samples_split=2,
                                         min_weight_fraction_leaf=0.0,
                                         presort='deprecated',
                                         random_state=None, splitter='best'),
              Dist=<class 'ngboost.distns.categorical.k_categorical.<locals>.Categorical'>,
              Score=<class 'ngboost.scores.LogScore'>, col_sample=1.0,
              learning_rate=0.01, minibatch_frac=1.0, n_estimators=100,
              natural_gradient=True,
              random_state=RandomState(MT1

In [204]:
from plot_utils import visualize_roc_curve
visualize_roc_curve(ngb_clf, df_train.values, y_train, df_test.values, y_test)

TRAIN: ROC AUC=0.835
TEST: ROC AUC=0.814


In [205]:
df_aux = pd.DataFrame(df_test.values, columns=cols_with_missing_indicators)
df_aux['predicted'] = generate_y_pred_with_custom_threshold(ngb_clf, df_test.values, 0.25)
df_aux['real'] = list(y_test)
df_aux['LoanPrincipal'] = df_aux.MonthlyIncome * 2
cost_score(df_aux.LoanPrincipal, df_aux.predicted, df_aux.real)

count_zero 4921
count_one 22079


1917134.7799999865

In [206]:
#FIX MEEEEEEEEEEE: REFACTOR PLZZ !!!
df_collector = pd.DataFrame(columns=  ["threshold", "cost", "train_auc", "test_auc"])
k = 0
for threshold in list(np.arange(0.05, 1, 0.05)):
    threshold = round(threshold,2)
    print("k: "+str(k))
    df_aux = pd.DataFrame(df_test.values, columns=cols_with_missing_indicators)
    df_aux['predicted'] = generate_y_pred_with_custom_threshold(ngb_clf, X_test, threshold)
    df_aux['real'] = list(y_test)
    df_aux['LoanPrincipal'] = df_aux.MonthlyIncome * 2
    print(threshold)
    print("cost "+str(cost_score(df_aux.LoanPrincipal, df_aux.predicted, df_aux.real)))
    print("th "+str(threshold))
    df_collector.ix[str(k),'threshold'] = threshold
    df_collector.ix[str(k),'cost'] = cost_score(df_aux.LoanPrincipal, df_aux.predicted, df_aux.real)
    k+=1
    print("sumando k")
    print("---------------------------------")


k: 0
count_zero 6
count_one 26994
0.05
cost 1975990.1999999885
th 0.05
sumando k
---------------------------------
k: 1
count_zero 494
count_one 26506
0.1
cost 1934855.0799999884
th 0.1
sumando k
---------------------------------
k: 2
count_zero 1914
count_one 25086
0.15
cost 1907305.519999986
th 0.15
sumando k
---------------------------------
k: 3
count_zero 3424
count_one 23576
0.2
cost 1909677.5399999868
th 0.2
sumando k
---------------------------------
k: 4
count_zero 4941
count_one 22059
0.25
cost 1909137.7399999858
th 0.25
sumando k
---------------------------------
k: 5
count_zero 6172
count_one 20828
0.3
cost 1983154.459999987
th 0.3
sumando k
---------------------------------
k: 6
count_zero 7476
count_one 19524
0.35
cost 2026049.3999999883
th 0.35
sumando k
---------------------------------
k: 7
count_zero 8894
count_one 18106
0.4
cost 2112190.67999999
th 0.4
sumando k
---------------------------------
k: 8
count_zero 9862
count_one 17138
0.45
cost 2141857.899999995
th 0.45

In [209]:

import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
def plot_trace_line_cost(df):
    """
    Plot lines with 'age' column as x axis and custom column (to compute sum/avg).
    
    Args:
        - df (pd.DataFrame): DataFrame to be represented
    """

    # Create and style traces
    trace0 = go.Scatter(
        x=df.threshold,
        y=df.cost,
        name="Responsible (target=0)",
        line=dict(color="rgb(86,157, 242)", width=4),
    )
    data = [trace0]

    # Edit the layout
    layout = dict(
        title="Evolution of cost according to thresholds",
        xaxis=dict(title="threshold"),
        yaxis=dict(title="cost")
    )

    fig = dict(data=data, layout=layout)
    iplot(fig)

In [210]:
plot_trace_line_cost(df_collector)

In [74]:
lista_probas = []
idx_p = 1
for p in list(ngb_clf.predict_proba(X_test)):
    lista_probas.append(p[idx_p])

In [76]:
len(lista_probas)

43310

In [142]:
pd.DataFrame(X_test)

0     1    2         3        4     5    6    7    8    9
0      0.524218  71.0  0.0  0.489049   4565.0   5.0  0.0  2.0  0.0  0.0
1      0.015158  67.0  0.0  0.003222   9000.0   6.0  0.0  0.0  0.0  1.0
2      0.004222  42.0  0.0  0.380055  11250.0   6.0  0.0  2.0  0.0  2.0
3      0.950403  45.0  0.0  0.468553  10000.0   8.0  0.0  3.0  0.0  2.0
4      0.031566  66.0  0.0  0.000000      0.0   9.0  0.0  1.0  0.0  0.0
...         ...   ...  ...       ...      ...   ...  ...  ...  ...  ...
26995  0.546383  30.0  0.0  0.829894   4167.0   6.0  0.0  2.0  0.0  2.0
26996  0.014533  57.0  0.0  0.008213   2556.0   3.0  0.0  0.0  0.0  0.0
26997  0.206702  41.0  0.0  0.307175   8333.0   6.0  0.0  1.0  0.0  2.0
26998  0.054332  40.0  0.0  0.248834      NaN   NaN  0.0  NaN  0.0  2.0
26999  0.948774  47.0  0.0  1.245648   1550.0  11.0  0.0  1.0  0.0  0.0

[27000 rows x 10 columns]

In [211]:
base0 = DecisionTreeRegressor(criterion="friedman_mse", max_depth=4)
base1 = DecisionTreeRegressor(criterion="friedman_mse", max_depth=6)
base2 = DecisionTreeRegressor(criterion="friedman_mse", max_depth=8)
base3 = DecisionTreeRegressor(criterion="friedman_mse", max_depth=12)

In [ ]:
def generate_y_pred_with_custom_threshold(model, x_data, threshold):
    """
    Generates new y_predictions according to a threshold.
    
    Args:
        - model (NGBoost model): NGBoost model that was trained.
        - x_data (np.ndarray): Data on which we predict probabilities
        - threshold (float): Float value to determine 1 or 0 for new predictions
    
    Returns updated y_predictions
    """
    y_predictions = model.predict_proba(x_data)
    y_pred = []
    count_zero = 0
    count_one = 0
    for i in range(len(list(y_predictions))):
        if y_predictions[i][1] > threshold:
            y_pred.append(0)
            count_zero += 1
        else:
            y_pred.append(1)
            count_one += 1
    print("count_zero " + str(count_zero))
    print("count_one " + str(count_one))
    return y_pred

In [ ]:
PRIMER EXPERIMENTO
THRESHOLD ERA PARA Y = 0 Y DIO UN VALOR DE 0.75 (P (X | Y) = 0)
NO TOMAMOS PROBAS PREDICHAS

In [ ]:
SEGUNDO EXPERIMENTO
THRESHOLD ERA PARA Y = 0 Y DIO VALORES 0.8, 0.85
PROBAS PREDICHAS POR NGBOOST PARA Y = 1

In [ ]:
SEGUNDO EXPERIMENTO
THRESHOLD Y = 0 O Y = 1??? POR QUE DEBERIA DAR MAYOR SI TOMO Y = 1, SI EN EL ANTEIROR EXPERIMENTO TOME Y=0.
RTA = Y = 1 (DELINQUIR, NO ASIGNO) E ITERO VALORES 0.7 A 0.9

In [ ]:
THRESHOLD Y = 1 || 0.7 Y 0.9

In [ ]:
#THRESHOLD: CONSIDERO YHAT = 0. Y TOMO VALORES DESDE 0.7 A 0.9. -- PROBAS POR THRESHOLD (CADA ROW, ME DA EL VALOR DE Y)
#PROBAS PREDICHAS POR NGBOOST PARA Y = 1. (ESTO ENTRA EN LA FORMULA DE UNA, PARAMETRO)

In [212]:
from utils import check_counts
count_zero, count_one = check_counts(ngb_clf, X_test, threshold)

In [213]:
count_zero

6

In [214]:
count_one

26994

In [217]:
#FIX MEEEEEEEEEEE: REFACTOR PLZZ !!!
df_collector = pd.DataFrame(columns=  ["alpha","hyperparams", "estimators", 
                                       "learning_rate", "max_depth", "threshold", "count_zero", "count_one",
                                       "cost", 
                                       "learning_cost",
                                       "train_auc", "test_auc"])
df_collector['hyperparams'] = df_collector['hyperparams'].astype('object')
k = 0
for estimator in [50, 75, 100, 120, 150, 200]:
    for lr in [0.01]:
        for baset in [base0,base1,base2,base3]:
            ngb_clf = NGBClassifier(Dist=Bernoulli,
                                      verbose=True, Base=baset, n_estimators = estimator, 
                                    learning_rate = lr, verbose_eval = 0
                                     )
            print(ngb_clf)
            ngb_clf.fit(X_train_resampled, y_train_resampled, sample_weight= get_sample_weights(y_train, y_train_resampled))
            index_th = 0
            #en el primer iteraba el threashold desde 0.1 a 0.9 obviamente cuanto mas menor me daba peor.. entonces itero
            #solamente d esde 0.70 a 0.95
            for kix in range(0,50):
                alpha = random.randint(10000, 180000)
                for threshold in list(np.arange(0.15, 0.4, 0.05)):
                    #alpha = random.randint(10000, 700000)
                    df_collector.ix[str(k),'alpha'] = alpha
                    df_collector.ix[str(k),'hyperparams'] = ngb_clf
                    df_collector.ix[str(k),'estimators'] = estimator
                    df_collector.ix[str(k),'learning_rate'] = lr
                    df_collector.ix[str(k),'max_depth'] = baset
                    threshold = round(threshold,2)
                    print("k: "+str(k))
                    df_aux = pd.DataFrame(X_test, columns=cols_with_missing_indicators)
                    df_aux['predicted'] = generate_y_pred_with_custom_threshold(ngb_clf, X_test, threshold)
                    df_aux['proba_predicted'] = [proba[1] for proba in ngb_clf.predict_proba(X_test)]
                    df_aux['real'] = list(y_test)
                    df_aux['LoanPrincipal'] = df_aux.MonthlyIncome * 2
                    print(threshold)
                    print("cost "+str(cost_score(df_aux.LoanPrincipal, df_aux.predicted, df_aux.real)))
                    print("th "+str(threshold))
                    df_collector.ix[str(k),'threshold'] = threshold
                    count_zero, count_one = check_counts(ngb_clf, X_test, threshold)
                    df_collector.ix[str(k),'count_zero'] = count_zero
                    df_collector.ix[str(k),'count_one'] = count_one
                    df_collector.ix[str(k),'cost'] = cost_score(df_aux.LoanPrincipal, df_aux.predicted, df_aux.real) #predicted tomo threshold (p(x|y=0))
                    df_collector.ix[str(k),'learning_cost'] = calculate_learning_cost(df_aux.predicted,df_aux.proba_predicted, alpha) #predicted tomo threshold (p(x|y=0)), probas predichas por el modelo para y = 1 y alpha
                    # predict probabilities
                    train_probs = ngb_clf.predict_proba(X_train)
                    test_probs = ngb_clf.predict_proba(X_test)
                    # keep probabilities for the positive outcome only
                    train_probs = train_probs[:, 1]
                    test_probs = test_probs[:, 1]
                    # calculate scores
                    train_auc = roc_auc_score(y_train, train_probs)
                    test_auc = roc_auc_score(y_test, test_probs)
                    df_collector.ix[str(k),'train_auc'] = train_auc
                    df_collector.ix[str(k),'test_auc'] = test_auc
                    k+=1
                    print("sumando k")
                    print("---------------------------------")
            del ngb_clf
df_collector['final_cost'] = df_collector['cost'] - df_collector['learning_cost']

NGBClassifier(Base=DecisionTreeRegressor(ccp_alpha=0.0,
                                         criterion='friedman_mse', max_depth=4,
                                         max_features=None, max_leaf_nodes=None,
                                         min_impurity_decrease=0.0,
                                         min_impurity_split=None,
                                         min_samples_leaf=1,
                                         min_samples_split=2,
                                         min_weight_fraction_leaf=0.0,
                                         presort='deprecated',
                                         random_state=None, splitter='best'),
              Dist=<class 'ngboost.distns.categorical.k_categorical.<locals>.Categorical'>,
              Score=<class 'ngboost.scores.LogScore'>, col_sample=1.0,
              learning_rate=0.01, minibatch_frac=1.0, n_estimators=50,
              natural_gradient=True,
              random_state=RandomState(MT19

0.25
cost 1983300.3799999908
th 0.25
sumando k
---------------------------------
k: 63
count_zero 0
count_one 27000
0.3
cost 1983300.3799999908
th 0.3
sumando k
---------------------------------
k: 64
count_zero 0
count_one 27000
0.35
cost 1983300.3799999908
th 0.35
sumando k
---------------------------------
k: 65
count_zero 0
count_one 27000
0.15
cost 1983300.3799999908
th 0.15
sumando k
---------------------------------
k: 66
count_zero 0
count_one 27000
0.2
cost 1983300.3799999908
th 0.2
sumando k
---------------------------------
k: 67
count_zero 0
count_one 27000
0.25
cost 1983300.3799999908
th 0.25
sumando k
---------------------------------
k: 68
count_zero 0
count_one 27000
0.3
cost 1983300.3799999908
th 0.3
sumando k
---------------------------------
k: 69
count_zero 0
count_one 27000
0.35
cost 1983300.3799999908
th 0.35
sumando k
---------------------------------
k: 70
count_zero 0
count_one 27000
0.15
cost 1983300.3799999908
th 0.15
sumando k
-------------------------------

0.3
cost 1983300.3799999908
th 0.3
sumando k
---------------------------------
k: 134
count_zero 0
count_one 27000
0.35
cost 1983300.3799999908
th 0.35
sumando k
---------------------------------
k: 135
count_zero 0
count_one 27000
0.15
cost 1983300.3799999908
th 0.15
sumando k
---------------------------------
k: 136
count_zero 0
count_one 27000
0.2
cost 1983300.3799999908
th 0.2
sumando k
---------------------------------
k: 137
count_zero 0
count_one 27000
0.25
cost 1983300.3799999908
th 0.25
sumando k
---------------------------------
k: 138
count_zero 0
count_one 27000
0.3
cost 1983300.3799999908
th 0.3
sumando k
---------------------------------
k: 139
count_zero 0
count_one 27000
0.35
cost 1983300.3799999908
th 0.35
sumando k
---------------------------------
k: 140
count_zero 0
count_one 27000
0.15
cost 1983300.3799999908
th 0.15
sumando k
---------------------------------
k: 141
count_zero 0
count_one 27000
0.2
cost 1983300.3799999908
th 0.2
sumando k
-------------------------

0.35
cost 1983300.3799999908
th 0.35
sumando k
---------------------------------
k: 205
count_zero 0
count_one 27000
0.15
cost 1983300.3799999908
th 0.15
sumando k
---------------------------------
k: 206
count_zero 0
count_one 27000
0.2
cost 1983300.3799999908
th 0.2
sumando k
---------------------------------
k: 207
count_zero 0
count_one 27000
0.25
cost 1983300.3799999908
th 0.25
sumando k
---------------------------------
k: 208
count_zero 0
count_one 27000
0.3
cost 1983300.3799999908
th 0.3
sumando k
---------------------------------
k: 209
count_zero 0
count_one 27000
0.35
cost 1983300.3799999908
th 0.35
sumando k
---------------------------------
k: 210
count_zero 0
count_one 27000
0.15
cost 1983300.3799999908
th 0.15
sumando k
---------------------------------
k: 211
count_zero 0
count_one 27000
0.2
cost 1983300.3799999908
th 0.2
sumando k
---------------------------------
k: 212
count_zero 0
count_one 27000
0.25
cost 1983300.3799999908
th 0.25
sumando k
-----------------------

sumando k
---------------------------------
k: 266
count_zero 0
count_one 27000
0.2
cost 1983300.3799999908
th 0.2
sumando k
---------------------------------
k: 267
count_zero 0
count_one 27000
0.25
cost 1983300.3799999908
th 0.25
sumando k
---------------------------------
k: 268
count_zero 332
count_one 26668
0.3
cost 1967078.1799999904
th 0.3
sumando k
---------------------------------
k: 269
count_zero 2383
count_one 24617
0.35
cost 1859867.5799999908
th 0.35
sumando k
---------------------------------
k: 270
count_zero 0
count_one 27000
0.15
cost 1983300.3799999908
th 0.15
sumando k
---------------------------------
k: 271
count_zero 0
count_one 27000
0.2
cost 1983300.3799999908
th 0.2
sumando k
---------------------------------
k: 272
count_zero 0
count_one 27000
0.25
cost 1983300.3799999908
th 0.25
sumando k
---------------------------------
k: 273
count_zero 332
count_one 26668
0.3
cost 1967078.1799999904
th 0.3
sumando k
---------------------------------
k: 274
count_zero 238

...

count_zero 10612
count_one 16388
0.2
cost 2750091.599999995
th 0.2
sumando k
---------------------------------
k: 4802
count_zero 11826
count_one 15174
0.25
cost 2965800.859999997
th 0.25
sumando k
---------------------------------
k: 4803
count_zero 12915
count_one 14085
0.3
cost 3140626.979999998
th 0.3
sumando k
---------------------------------
k: 4804
count_zero 13991
count_one 13009
0.35
cost 3484458.939999997
th 0.35
sumando k
---------------------------------
k: 4805
count_zero 9172
count_one 17828
0.15
cost 2429274.779999999
th 0.15
sumando k
---------------------------------
k: 4806
count_zero 10612
count_one 16388
0.2
cost 2750091.599999995
th 0.2
sumando k
---------------------------------
k: 4807
count_zero 11826
count_one 15174
0.25
cost 2965800.859999997
th 0.25
sumando k
---------------------------------
k: 4808
count_zero 12915
count_one 14085
0.3
cost 3140626.979999998
th 0.3
sumando k
---------------------------------
k: 4809
count_zero 13991
count_one 13009
0.35
cos

cost 3484458.939999997
th 0.35
sumando k
---------------------------------
k: 4870
count_zero 9172
count_one 17828
0.15
cost 2429274.779999999
th 0.15
sumando k
---------------------------------
k: 4871
count_zero 10612
count_one 16388
0.2
cost 2750091.599999995
th 0.2
sumando k
---------------------------------
k: 4872
count_zero 11826
count_one 15174
0.25
cost 2965800.859999997
th 0.25
sumando k
---------------------------------
k: 4873
count_zero 12915
count_one 14085
0.3
cost 3140626.979999998
th 0.3
sumando k
---------------------------------
k: 4874
count_zero 13991
count_one 13009
0.35
cost 3484458.939999997
th 0.35
sumando k
---------------------------------
k: 4875
count_zero 9172
count_one 17828
0.15
cost 2429274.779999999
th 0.15
sumando k
---------------------------------
k: 4876
count_zero 10612
count_one 16388
0.2
cost 2750091.599999995
th 0.2
sumando k
---------------------------------
k: 4877
count_zero 11826
count_one 15174
0.25
cost 2965800.859999997
th 0.25
sumando k

count_zero 12915
count_one 14085
0.3
cost 3140626.979999998
th 0.3
sumando k
---------------------------------
k: 4939
count_zero 13991
count_one 13009
0.35
cost 3484458.939999997
th 0.35
sumando k
---------------------------------
k: 4940
count_zero 9172
count_one 17828
0.15
cost 2429274.779999999
th 0.15
sumando k
---------------------------------
k: 4941
count_zero 10612
count_one 16388
0.2
cost 2750091.599999995
th 0.2
sumando k
---------------------------------
k: 4942
count_zero 11826
count_one 15174
0.25
cost 2965800.859999997
th 0.25
sumando k
---------------------------------
k: 4943
count_zero 12915
count_one 14085
0.3
cost 3140626.979999998
th 0.3
sumando k
---------------------------------
k: 4944
count_zero 13991
count_one 13009
0.35
cost 3484458.939999997
th 0.35
sumando k
---------------------------------
k: 4945
count_zero 9172
count_one 17828
0.15
cost 2429274.779999999
th 0.15
sumando k
---------------------------------
k: 4946
count_zero 10612
count_one 16388
0.2
cos

k: 5000
count_zero 0
count_one 27000
0.15
cost 1983300.3799999908
th 0.15
sumando k
---------------------------------
k: 5001
count_zero 0
count_one 27000
0.2
cost 1983300.3799999908
th 0.2
sumando k
---------------------------------
k: 5002
count_zero 0
count_one 27000
0.25
cost 1983300.3799999908
th 0.25
sumando k
---------------------------------
k: 5003
count_zero 0
count_one 27000
0.3
cost 1983300.3799999908
th 0.3
sumando k
---------------------------------
k: 5004
count_zero 0
count_one 27000
0.35
cost 1983300.3799999908
th 0.35
sumando k
---------------------------------
k: 5005
count_zero 0
count_one 27000
0.15
cost 1983300.3799999908
th 0.15
sumando k
---------------------------------
k: 5006
count_zero 0
count_one 27000
0.2
cost 1983300.3799999908
th 0.2
sumando k
---------------------------------
k: 5007
count_zero 0
count_one 27000
0.25
cost 1983300.3799999908
th 0.25
sumando k
---------------------------------
k: 5008
count_zero 0
count_one 27000
0.3
cost 1983300.37999999

KeyboardInterrupt: 

In [218]:
df_collector['final_cost'] = df_collector['cost'] - df_collector['learning_cost']

In [220]:
df_collector['diff_auc'] = df_collector['train_auc'] - df_collector['test_auc']

In [226]:
df_collector['max_depth'] = [md.max_depth for md in df_collector['max_depth']]

In [231]:
del df_collector['hyperparams']

In [232]:
df_collector.sort_values("final_cost", ascending=False).head(20)

alpha estimators learning_rate  max_depth threshold count_zero  \
0      37676         50          0.01          4      0.15      24158   
2061   38910        100          0.01          4       0.2      14278   
2091  149725        100          0.01          4       0.2      14278   
2090  149725        100          0.01          4      0.15      17122   
2089   11957        100          0.01          4      0.35       9979   
2088   11957        100          0.01          4       0.3      11514   
2087   11957        100          0.01          4      0.25      13034   
2086   11957        100          0.01          4       0.2      14278   
2085   11957        100          0.01          4      0.15      17122   
2084   77037        100          0.01          4      0.35       9979   
2083   77037        100          0.01          4       0.3      11514   
2082   77037        100          0.01          4      0.25      13034   
2081   77037        100          0.01          4       0.2      14278   
2080   77037        100          0.01          4      0.15      17122   
2079  162605        100          0.01          4      0.35       9979   
2078  162605        100          0.01          4       0.3      11514   
2077  162605        100          0.01          4      0.25      13034   
2076  162605        100          0.01          4       0.2      14278   
2075  162605        100          0.01          4      0.15      17122   
2074  159380        100          0.01          4      0.35       9979   

     count_one        cost learning_cost train_auc  test_auc  final_cost  \
0         2842  1.9833e+06             0  0.826083  0.824467  1.9833e+06   
2061     12722  1.9833e+06             0  0.827736  0.826728  1.9833e+06   
2091     12722  1.9833e+06             0  0.827736  0.826728  1.9833e+06   
2090      9878  1.9833e+06             0  0.827736  0.826728  1.9833e+06   
2089     17021  1.9833e+06             0  0.827736  0.826728  1.9833e+06   
2088     15486  1.9833e+06             0  0.827736  0.826728  1.9833e+06   
2087     13966  1.9833e+06             0  0.827736  0.826728  1.9833e+06   
2086     12722  1.9833e+06             0  0.827736  0.826728  1.9833e+06   
2085      9878  1.9833e+06             0  0.827736  0.826728  1.9833e+06   
2084     17021  1.9833e+06             0  0.827736  0.826728  1.9833e+06   
2083     15486  1.9833e+06             0  0.827736  0.826728  1.9833e+06   
2082     13966  1.9833e+06             0  0.827736  0.826728  1.9833e+06   
2081     12722  1.9833e+06             0  0.827736  0.826728  1.9833e+06   
2080      9878  1.9833e+06             0  0.827736  0.826728  1.9833e+06   
2079     17021  1.9833e+06             0  0.827736  0.826728  1.9833e+06   
2078     15486  1.9833e+06             0  0.827736  0.826728  1.9833e+06   
2077     13966  1.9833e+06             0  0.827736  0.826728  1.9833e+06   
2076     12722  1.9833e+06             0  0.827736  0.826728  1.9833e+06   
2075      9878  1.9833e+06             0  0.827736  0.826728  1.9833e+06   
2074     17021  1.9833e+06             0  0.827736  0.826728  1.9833e+06   

        diff_auc  
0      0.0016167  
2061  0.00100799  
2091  0.00100799  
2090  0.00100799  
2089  0.00100799  
2088  0.00100799  
2087  0.00100799  
2086  0.00100799  
2085  0.00100799  
2084  0.00100799  
2083  0.00100799  
2082  0.00100799  
2081  0.00100799  
2080  0.00100799  
2079  0.00100799  
2078  0.00100799  
2077  0.00100799  
2076  0.00100799  
2075  0.00100799  
2074  0.00100799

In [3]:
import pandas as pd
df_collector = pd.read_csv("results_2exp_1rstpart.csv")

In [147]:
df_collector['final_cost'] = df_collector['cost'] - df_collector['learning_cost']

In [157]:
df_collector.to_csv("raw_models_second_experiment.csv", index=False)

In [160]:
df_analysis = df_collector[(df_collector['final_cost'] >0) & (df_collector['learning_cost'] >0) & (df_collector['final_cost'] >800000)].sort_values("final_cost").reset_index(drop=True)

In [161]:
df_analysis

alpha                                        hyperparams estimators  \
0   322247  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
1   317847  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
2   158285  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         75   
3    71990  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         75   
4    16394  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
5   185450  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        100   
6   304167  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
7   300535  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
8    22964  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
9   149811  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         75   
10   15193  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
11   31829  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        120   
12  164985  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        100   
13  275348  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
14  275138  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
15  274607  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
16   53575  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
17  268878  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
18  127567  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         75   
19  254955  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
20  126762  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         75   
21   56190  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         75   
22   47142  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
23   54744  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         75   
24  223668  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
25   23406  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        120   
26  104294  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         75   
27   40041  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
28   42876  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         75   
29  109646  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        100   
30   89873  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         75   
31  108128  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        100   
32   87106  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         75   
33  176481  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
34  170060  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
35  152264  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
36   83183  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        100   
37   14789  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        120   
38  134953  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
39  124487  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
40   54330  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         75   
41  110188  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
42   49171  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         75   
43   91445  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
44   85457  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   
45   25051  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         75   
46   11679  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         75   
47   31000  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        100   
48   25348  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        100   
49   17139  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         75   
50   12408  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         75   
51   24928  NGBClassifier(Base=DecisionTreeRegressor(

In [162]:
df_analysis.to_csv("data_processed_models.csv", index=False)

In [ ]:
df_analysis

In [93]:
df_collector['final_cost'] = df_collector['cost'] - df_collector['learning_cost']

In [107]:
df_collector[df_collector['final_cost'] >0].query("alpha==999725")

alpha                                        hyperparams estimators  \
3272  999725  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         50   

     learning_rate                                          max_depth  \
3272          0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   

     threshold         cost learning_cost train_auc  test_auc   final_cost  
3272       0.8  2.47167e+06             0  0.826416  0.824224  2.47167e+06

In [112]:
df_collector[df_collector['final_cost'] >0].describe()

alpha                                        hyperparams  estimators  \
count      837                                                837         837   
unique     835                                                  8           1   
top     386018  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
freq         2                                                401         837   

        learning_rate                                          max_depth  \
count          837.00                                                837   
unique           3.00                                                  4   
top              0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
freq           711.00                                                520   

        threshold       cost  learning_cost   train_auc    test_auc  \
count       837.0      837.0          837.0  837.000000  837.000000   
unique        7.0       12.0          226.0    8.000000    8.000000   
top           0.9  2471674.1            0.0    0.826416    0.824224   
freq        316.0      612.0          612.0  401.000000  401.000000   

        final_cost  
count        837.0  
unique       226.0  
top      2471674.1  
freq         612.0

In [102]:
df_collector[df_collector['final_cost'] >0].min().alpha

10079.0

In [86]:
df_collector.sort_values("cost").iloc[3051]

alpha                                                              596272
hyperparams             NGBClassifier(Base=DecisionTreeRegressor(ccp_a...
estimators                                                             90
learning_rate                                                         0.1
max_depth               DecisionTreeRegressor(ccp_alpha=0.0, criterion...
threshold                                                            0.75
cost                                                          5.70545e+06
cost_common                                                    7.6209e+06
learning_cost                                                 4.20081e+08
learning_cost_common                                          9.54968e+08
train_auc                                                         0.94028
test_auc                                                         0.762959
Name: 1952, dtype: object

In [88]:
df_collector.sort_values("cost").iloc[3051].cost - df_collector.sort_values("cost").iloc[3051].learning_cost

-414375074.8010962

In [20]:
df_analysis = pd.read_csv("data_processed_models.csv")

In [22]:
df_analysis['diff_auc'] = df_analysis['train_auc'] - df_analysis['test_auc']

In [23]:
df_analysis

alpha                                        hyperparams  estimators  \
0   322247  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
1   317847  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
2   158285  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
3    71990  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
4    16394  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
5   185450  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
6   304167  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
7   300535  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
8    22964  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         150   
9   149811  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
10   15193  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
11   31829  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
12  164985  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
13  275348  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
14  275138  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
15  274607  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
16   53575  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
17  268878  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
18  127567  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
19  254955  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
20  126762  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
21   56190  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
22   47142  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
23   54744  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
24  223668  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
25   23406  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
26  104294  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
27   40041  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
28   42876  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
29  109646  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
30   89873  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
31  108128  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
32   87106  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
33  176481  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
34  170060  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
35  152264  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
36   83183  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
37   14789  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
38  134953  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
39  124487  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
40   54330  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
41  110188  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
42   49171  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
43   91445  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
44   85457  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
45   25051  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
46   11679  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
47   31000  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
48   25348  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
49   17139  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
50   12408  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
5

In [24]:
df_analysis.sort_values("diff_auc")

alpha                                        hyperparams  estimators  \
10   15193  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
4    16394  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
36   83183  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
29  109646  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
5   185450  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
31  108128  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
48   25348  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
47   31000  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
12  164985  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
25   23406  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
11   31829  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
37   14789  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
8    22964  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         150   
46   11679  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
3    71990  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
28   42876  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
23   54744  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
21   56190  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
30   89873  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
32   87106  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
40   54330  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
42   49171  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
26  104294  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
20  126762  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
45   25051  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
9   149811  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
49   17139  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
2   158285  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
50   12408  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
18  127567  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
27   40041  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
16   53575  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
22   47142  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
43   91445  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
44   85457  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
41  110188  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
39  124487  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
38  134953  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
0   322247  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
34  170060  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
33  176481  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
51   24928  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
24  223668  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
19  254955  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
17  268878  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
15  274607  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
14  275138  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
13  275348  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
7   300535  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
6   304167  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
1   317847  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
3

In [76]:
df_analysis = pd.read_csv("top30_models.csv")

In [71]:
df_analysis = df_analysis.sort_values("diff_auc").head(30)

In [72]:
df_analysis[df_analysis['threshold'] >= 0.8].sort_values("diff_auc").head(28)

alpha                                        hyperparams  estimators  \
36   83183  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
29  109646  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
5   185450  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
31  108128  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
48   25348  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
47   31000  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
12  164985  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
25   23406  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
11   31829  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
37   14789  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
8    22964  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         150   
21   56190  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
23   54744  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
28   42876  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
3    71990  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
46   11679  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
30   89873  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
32   87106  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
40   54330  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
42   49171  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
26  104294  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
20  126762  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
45   25051  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
9   149811  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
49   17139  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
2   158285  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
50   12408  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
18  127567  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   

    learning_rate max_depth  threshold        cost  learning_cost  train_auc  \
36           0.01      None       0.85  1987263.76   5.061557e+05   0.829214   
29           0.01      None       0.85  1987263.76   6.671789e+05   0.829214   
5            0.01      None       0.85  1987263.76   1.128435e+06   0.829214   
31           0.01      None       0.85  1987263.76   6.579421e+05   0.829214   
48           0.01      None       0.85  1987263.76   1.542387e+05   0.829214   
47           0.01      None       0.85  1987263.76   1.886302e+05   0.829214   
12           0.01      None       0.85  1987263.76   1.003908e+06   0.829214   
25           0.01      None       0.85  1980368.94   7.571576e+05   0.829289   
11           0.01      None       0.85  1980368.94   1.029632e+06   0.829289   
37           0.01      None       0.85  1980368.94   4.784074e+05   0.829289   
8            0.01      None       0.85  1966387.00   1.076402e+06   0.829275   
21           0.01      None       0.80  1980286.78   8.821657e+05   0.828108   
23           0.01      None       0.80  1980286.78   8.594639e+05   0.828108   
28           0.01      None       0.80  1980286.78   6.731400e+05   0.828108   
3            0.01      None       0.80  1980286.78   1.130221e+06   0.828108   
46           0.01      None       0.80  1980286.78   1.833567e+05   0.828108   
30           0.01      None       0.90  1972517.68   6.450023e+05   0.832750   
32           0.01      None       0.90  1972517.68   6.251440e+05   0.832750   
40           0.01      None       0.90  1972517.68   3.899166e+05   0.832750   
42           0.01      None       0.90  1972517.68   3.528914e+05   0.832750   
26           0.01      None       0.90  1972517.68   7.484992e+05   0.832750   
20         

In [ ]:
estimators: 75 a 200
learning_rate 0.01
threshold 0.85

In [67]:
df_analysis['max_depth'] = [DecisionTreeRegressor(cc).max_depth for cc in list(df_analysis['max_depth'])]

In [84]:
df_analysis.hyperparams.iloc[0]

"NGBClassifier(Base=DecisionTreeRegressor(ccp_alpha=0.0,\n                                         criterion='friedman_mse', max_depth=6,\n                                         max_features=None, max_leaf_nodes=None,\n                                         min_impurity_decrease=0.0,\n                                         min_impurity_split=None,\n                                         min_samples_leaf=1,\n                                         min_samples_split=2,\n                                         min_weight_fraction_leaf=0.0,\n                                         presort='deprecated',\n                                         random_state=None, splitter='best'),\n              Dist=<class 'ngboost.distns.categorical.k_categorical.<locals>.Categorical'>,\n              Score=<class 'ngboost.scores.LogScore'>, col_sample=1.0,\n              learning_rate=0.01, minibatch_frac=1.0, n_estimators=50,\n              natural_gradient=True,\n              random_state=R

In [106]:
df_analysis[(df_analysis['threshold'] == 0.8) |(df_analysis['threshold'] == 0.85)].sort_values(['final_cost']).alpha.unique()

array([ 71990, 185450,  22964,  31829, 164985,  56190,  54744,  23406,
        42876, 109646, 108128,  83183,  14789,  11679,  31000,  25348])

In [107]:
base0 = DecisionTreeRegressor(criterion="friedman_mse", max_depth=4)
base1 = DecisionTreeRegressor(criterion="friedman_mse", max_depth=6)

In [26]:
def check_counts(model, x_data, threshold):
    y_predictions = model.predict_proba(x_data)
    y_pred = []
    count_zero = 0
    count_one = 0
    for i in range(len(list(y_predictions))):
        if y_predictions[i][0] > threshold:
            y_pred.append(0)
            count_zero += 1
        else:
            y_pred.append(1)
            count_one += 1
    return count_zero, count_one

In [114]:
#FIX MEEEEEEEEEEE: REFACTOR PLZZ !!!
df_collector = pd.DataFrame(columns=  ["alpha","hyperparams", "estimators", 
                                       "learning_rate", "max_depth", "threshold", 
                                       "cost", 
                                       "learning_cost",
                                       "train_auc", "test_auc"])
df_collector['hyperparams'] = df_collector['hyperparams'].astype('object')
k = 0
for estimator in [75, 100, 125, 150, 175, 200]:
    for lr in [0.01]:
        for baset in [base0,base1]:
            ngb_clf = NGBClassifier(Dist=Bernoulli,
                                      verbose=True, Base=baset, n_estimators = estimator, 
                                    learning_rate = lr, verbose_eval = 0
                                     )
            print(ngb_clf)
            ngb_clf.fit(X_train_resampled, y_train_resampled, sample_weight= get_sample_weights(y_train, y_train_resampled))
            index_th = 0
            #en el primer iteraba el threashold desde 0.1 a 0.9 obviamente cuanto mas menor me daba peor.. entonces itero
            #solamente d esde 0.70 a 0.95
            for threshold in list(np.arange(0.75, 0.95, 0.025)):
                count_zero, count_one = check_counts(ngb_clf, df_test.values, threshold)
                if count_zero == 0:
                    pass
                else:
                    for kix in range(0,50):
                        alpha = random.randint(20000, 140000)
                        #alpha = random.randint(10000, 700000)
                        df_collector.ix[str(k),'alpha'] = alpha
                        df_collector.ix[str(k),'hyperparams'] = ngb_clf
                        df_collector.ix[str(k),'estimators'] = estimator
                        df_collector.ix[str(k),'learning_rate'] = lr
                        df_collector.ix[str(k),'max_depth'] = baset
                        threshold = round(threshold,2)
                        print("k: "+str(k))
                        df_aux = pd.DataFrame(df_test.values, columns=cols_with_missing_indicators)
                        df_aux['predicted'] = generate_y_pred_with_custom_threshold(ngb_clf, df_test.values, threshold)
                        df_aux['proba_predicted'] = [proba[1] for proba in ngb_clf.predict_proba(df_test.values)]
                        df_aux['real'] = list(y_test)
                        df_aux['LoanPrincipal'] = df_aux.MonthlyIncome * 2
                        print(threshold)
                        print("cost "+str(cost_score(df_aux.LoanPrincipal, df_aux.predicted, df_aux.real)))
                        print("th "+str(threshold))
                        df_collector.ix[str(k),'threshold'] = threshold
                        df_collector.ix[str(k),'cost'] = cost_score(df_aux.LoanPrincipal, df_aux.predicted, df_aux.real)
                        df_collector.ix[str(k),'learning_cost'] = calculate_learning_cost(df_aux.predicted,df_aux.proba_predicted, alpha)
                        # predict probabilities
                        train_probs = ngb_clf.predict_proba(df_train.values)
                        test_probs = ngb_clf.predict_proba(df_test.values)
                        # keep probabilities for the positive outcome only
                        train_probs = train_probs[:, 1]
                        test_probs = test_probs[:, 1]
                        # calculate scores
                        train_auc = roc_auc_score(y_train, train_probs)
                        test_auc = roc_auc_score(y_test, test_probs)
                        df_collector.ix[str(k),'train_auc'] = train_auc
                        df_collector.ix[str(k),'test_auc'] = test_auc
                        k+=1
                        print("sumando k")
                        print("---------------------------------")
            del ngb_clf
df_collector['final_cost'] = df_collector['cost'] - df_collector['learning_cost']

NGBClassifier(Base=DecisionTreeRegressor(ccp_alpha=0.0,
                                         criterion='friedman_mse', max_depth=4,
                                         max_features=None, max_leaf_nodes=None,
                                         min_impurity_decrease=0.0,
                                         min_impurity_split=None,
                                         min_samples_leaf=1,
                                         min_samples_split=2,
                                         min_weight_fraction_leaf=0.0,
                                         presort='deprecated',
                                         random_state=None, splitter='best'),
              Dist=<class 'ngboost.distns.categorical.k_categorical.<locals>.Categorical'>,
              Score=<class 'ngboost.scores.LogScore'>, col_sample=1.0,
              learning_rate=0.01, minibatch_frac=1.0, n_estimators=75,
              natural_gradient=True,
              random_state=RandomState(MT19

0.78
cost 1964467.519999986
th 0.78
sumando k
---------------------------------
k: 52
count_zero 84
count_one 26916
0.78
cost 1964467.519999986
th 0.78
sumando k
---------------------------------
k: 53
count_zero 84
count_one 26916
0.78
cost 1964467.519999986
th 0.78
sumando k
---------------------------------
k: 54
count_zero 84
count_one 26916
0.78
cost 1964467.519999986
th 0.78
sumando k
---------------------------------
k: 55
count_zero 84
count_one 26916
0.78
cost 1964467.519999986
th 0.78
sumando k
---------------------------------
k: 56
count_zero 84
count_one 26916
0.78
cost 1964467.519999986
th 0.78
sumando k
---------------------------------
k: 57
count_zero 84
count_one 26916
0.78
cost 1964467.519999986
th 0.78
sumando k
---------------------------------
k: 58
count_zero 84
count_one 26916
0.78
cost 1964467.519999986
th 0.78
sumando k
---------------------------------
k: 59
count_zero 84
count_one 26916
0.78
cost 1964467.519999986
th 0.78
sumando k
--------------------------

0.75
cost 1875663.8199999873
th 0.75
sumando k
---------------------------------
k: 104
count_zero 993
count_one 26007
0.75
cost 1875663.8199999873
th 0.75
sumando k
---------------------------------
k: 105
count_zero 993
count_one 26007
0.75
cost 1875663.8199999873
th 0.75
sumando k
---------------------------------
k: 106
count_zero 993
count_one 26007
0.75
cost 1875663.8199999873
th 0.75
sumando k
---------------------------------
k: 107
count_zero 993
count_one 26007
0.75
cost 1875663.8199999873
th 0.75
sumando k
---------------------------------
k: 108
count_zero 993
count_one 26007
0.75
cost 1875663.8199999873
th 0.75
sumando k
---------------------------------
k: 109
count_zero 993
count_one 26007
0.75
cost 1875663.8199999873
th 0.75
sumando k
---------------------------------
k: 110
count_zero 993
count_one 26007
0.75
cost 1875663.8199999873
th 0.75
sumando k
---------------------------------
k: 111
count_zero 993
count_one 26007
0.75
cost 1875663.8199999873
th 0.75
sumando k
-

0.78
cost 1930539.4199999874
th 0.78
sumando k
---------------------------------
k: 173
count_zero 372
count_one 26628
0.78
cost 1930539.4199999874
th 0.78
sumando k
---------------------------------
k: 174
count_zero 372
count_one 26628
0.78
cost 1930539.4199999874
th 0.78
sumando k
---------------------------------
k: 175
count_zero 372
count_one 26628
0.78
cost 1930539.4199999874
th 0.78
sumando k
---------------------------------
k: 176
count_zero 372
count_one 26628
0.78
cost 1930539.4199999874
th 0.78
sumando k
---------------------------------
k: 177
count_zero 372
count_one 26628
0.78
cost 1930539.4199999874
th 0.78
sumando k
---------------------------------
k: 178
count_zero 372
count_one 26628
0.78
cost 1930539.4199999874
th 0.78
sumando k
---------------------------------
k: 179
count_zero 372
count_one 26628
0.78
cost 1930539.4199999874
th 0.78
sumando k
---------------------------------
k: 180
count_zero 372
count_one 26628
0.78
cost 1930539.4199999874
th 0.78
sumando k
-

0.8
cost 1954609.739999987
th 0.8
sumando k
---------------------------------
k: 243
count_zero 236
count_one 26764
0.8
cost 1954609.739999987
th 0.8
sumando k
---------------------------------
k: 244
count_zero 236
count_one 26764
0.8
cost 1954609.739999987
th 0.8
sumando k
---------------------------------
k: 245
count_zero 236
count_one 26764
0.8
cost 1954609.739999987
th 0.8
sumando k
---------------------------------
k: 246
count_zero 236
count_one 26764
0.8
cost 1954609.739999987
th 0.8
sumando k
---------------------------------
k: 247
count_zero 236
count_one 26764
0.8
cost 1954609.739999987
th 0.8
sumando k
---------------------------------
k: 248
count_zero 236
count_one 26764
0.8
cost 1954609.739999987
th 0.8
sumando k
---------------------------------
k: 249
count_zero 236
count_one 26764
0.8
cost 1954609.739999987
th 0.8
sumando k
---------------------------------
k: 250
count_zero 42
count_one 26958
0.82
cost 1971846.7999999858
th 0.82
sumando k
--------------------------

...

sumando k
---------------------------------
k: 958
count_zero 88
count_one 26912
0.85
cost 1970740.9199999855
th 0.85
sumando k
---------------------------------
k: 959
count_zero 88
count_one 26912
0.85
cost 1970740.9199999855
th 0.85
sumando k
---------------------------------
k: 960
count_zero 88
count_one 26912
0.85
cost 1970740.9199999855
th 0.85
sumando k
---------------------------------
k: 961
count_zero 88
count_one 26912
0.85
cost 1970740.9199999855
th 0.85
sumando k
---------------------------------
k: 962
count_zero 88
count_one 26912
0.85
cost 1970740.9199999855
th 0.85
sumando k
---------------------------------
k: 963
count_zero 88
count_one 26912
0.85
cost 1970740.9199999855
th 0.85
sumando k
---------------------------------
k: 964
count_zero 88
count_one 26912
0.85
cost 1970740.9199999855
th 0.85
sumando k
---------------------------------
k: 965
count_zero 88
count_one 26912
0.85
cost 1970740.9199999855
th 0.85
sumando k
---------------------------------
k: 966
count

sumando k
---------------------------------
k: 1009
count_zero 2078
count_one 24922
0.75
cost 1853400.9199999867
th 0.75
sumando k
---------------------------------
k: 1010
count_zero 2078
count_one 24922
0.75
cost 1853400.9199999867
th 0.75
sumando k
---------------------------------
k: 1011
count_zero 2078
count_one 24922
0.75
cost 1853400.9199999867
th 0.75
sumando k
---------------------------------
k: 1012
count_zero 2078
count_one 24922
0.75
cost 1853400.9199999867
th 0.75
sumando k
---------------------------------
k: 1013
count_zero 2078
count_one 24922
0.75
cost 1853400.9199999867
th 0.75
sumando k
---------------------------------
k: 1014
count_zero 2078
count_one 24922
0.75
cost 1853400.9199999867
th 0.75
sumando k
---------------------------------
k: 1015
count_zero 2078
count_one 24922
0.75
cost 1853400.9199999867
th 0.75
sumando k
---------------------------------
k: 1016
count_zero 2078
count_one 24922
0.75
cost 1853400.9199999867
th 0.75
sumando k
----------------------

cost 1874679.9999999881
th 0.78
sumando k
---------------------------------
k: 1077
count_zero 1180
count_one 25820
0.78
cost 1874679.9999999881
th 0.78
sumando k
---------------------------------
k: 1078
count_zero 1180
count_one 25820
0.78
cost 1874679.9999999881
th 0.78
sumando k
---------------------------------
k: 1079
count_zero 1180
count_one 25820
0.78
cost 1874679.9999999881
th 0.78
sumando k
---------------------------------
k: 1080
count_zero 1180
count_one 25820
0.78
cost 1874679.9999999881
th 0.78
sumando k
---------------------------------
k: 1081
count_zero 1180
count_one 25820
0.78
cost 1874679.9999999881
th 0.78
sumando k
---------------------------------
k: 1082
count_zero 1180
count_one 25820
0.78
cost 1874679.9999999881
th 0.78
sumando k
---------------------------------
k: 1083
count_zero 1180
count_one 25820
0.78
cost 1874679.9999999881
th 0.78
sumando k
---------------------------------
k: 1084
count_zero 1180
count_one 25820
0.78
cost 1874679.9999999881
th 0.78


0.8
cost 1882106.9599999865
th 0.8
sumando k
---------------------------------
k: 1146
count_zero 837
count_one 26163
0.8
cost 1882106.9599999865
th 0.8
sumando k
---------------------------------
k: 1147
count_zero 837
count_one 26163
0.8
cost 1882106.9599999865
th 0.8
sumando k
---------------------------------
k: 1148
count_zero 837
count_one 26163
0.8
cost 1882106.9599999865
th 0.8
sumando k
---------------------------------
k: 1149
count_zero 837
count_one 26163
0.8
cost 1882106.9599999865
th 0.8
sumando k
---------------------------------
k: 1150
count_zero 544
count_one 26456
0.82
cost 1918524.9799999886
th 0.82
sumando k
---------------------------------
k: 1151
count_zero 544
count_one 26456
0.82
cost 1918524.9799999886
th 0.82
sumando k
---------------------------------
k: 1152
count_zero 544
count_one 26456
0.82
cost 1918524.9799999886
th 0.82
sumando k
---------------------------------
k: 1153
count_zero 544
count_one 26456
0.82
cost 1918524.9799999886
th 0.82
sumando k
---

count_zero 196
count_one 26804
0.85
cost 1954134.3199999868
th 0.85
sumando k
---------------------------------
k: 1215
count_zero 196
count_one 26804
0.85
cost 1954134.3199999868
th 0.85
sumando k
---------------------------------
k: 1216
count_zero 196
count_one 26804
0.85
cost 1954134.3199999868
th 0.85
sumando k
---------------------------------
k: 1217
count_zero 196
count_one 26804
0.85
cost 1954134.3199999868
th 0.85
sumando k
---------------------------------
k: 1218
count_zero 196
count_one 26804
0.85
cost 1954134.3199999868
th 0.85
sumando k
---------------------------------
k: 1219
count_zero 196
count_one 26804
0.85
cost 1954134.3199999868
th 0.85
sumando k
---------------------------------
k: 1220
count_zero 196
count_one 26804
0.85
cost 1954134.3199999868
th 0.85
sumando k
---------------------------------
k: 1221
count_zero 196
count_one 26804
0.85
cost 1954134.3199999868
th 0.85
sumando k
---------------------------------
k: 1222
count_zero 196
count_one 26804
0.85
cost

In [117]:
df_collector['diff_auc'] = df_collector['train_auc'] - df_collector['test_auc']
df_collector[(df_collector["final_cost"] > 0)].sort_values(['final_cost'])

alpha                                        hyperparams estimators  \
1207  82148  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        200   
1222  81924  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        200   
495   85982  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        125   
1220  81615  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        200   
444   43195  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        125   
...     ...                                                ...        ...   
723   26541  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
721   25104  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
745   23110  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
705   22034  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
741   20896  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   

     learning_rate                                          max_depth  \
1207          0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
1222          0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
495           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
1220          0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
444           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
...            ...                                                ...   
723           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
721           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
745           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
705           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
741           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   

     threshold         cost learning_cost train_auc  test_auc   final_cost  \
1207      0.85  1.95413e+06   1.95261e+06  0.829057  0.825046      1523.36   
1222      0.85  1.95413e+06   1.94729e+06  0.829057  0.825046      6847.71   
495       0.82  1.96346e+06   1.95467e+06   0.82949  0.825923      8783.25   
1220      0.85  1.95413e+06   1.93994e+06  0.829057  0.825046      14192.5   
444        0.8  1.93946e+06   1.91155e+06   0.82949  0.825923      27906.9   
...        ...          ...           ...       ...       ...          ...   
723       0.85   1.9787e+06       3265.52  0.829286  0.825548  1.97543e+06   
721       0.85   1.9787e+06       3088.72  0.829286  0.825548  1.97561e+06   
745       0.85   1.9787e+06       2843.38  0.829286  0.825548  1.97585e+06   
705       0.85   1.9787e+06       2710.99  0.829286  0.825548  1.97599e+06   
741       0.85   1.9787e+06       2570.98  0.829286  0.825548  1.97613e+06   

        diff_auc  
1207  0.00401119  
1222  0.00401119  
495   0.00356673  
1220  0.00401119  
444   0.00356673  
...          ...  
723   0.00373749  
721   0.00373749  
745   0.00373749  
705   0.00373749  
741   0.00373749  

[321 rows x 12 columns]

In [158]:
df_collector[(df_collector["final_cost"] > 0)].sort_values(['final_cost'], ascending=False).head(50)

alpha                                        hyperparams estimators  \
741   20896  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
705   22034  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
745   23110  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
721   25104  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
723   26541  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
717   31336  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
722   33043  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
715   37349  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
748   40767  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
712   45676  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
708   45750  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
707   45967  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
719   46158  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
720   46858  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
701   48291  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
710   52017  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
727   52222  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
716   52539  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
711   53989  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
742   64365  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
726   64852  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
731   67884  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
744   69691  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
704   72648  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
733   74012  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
725   74383  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
702   79059  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
736   83596  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
737   87231  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
746   91027  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
706   91899  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
729   96341  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
734   96490  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
713   98599  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
749   98788  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
700  101893  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
740  111470  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
728  112771  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
735  115386  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
714  115866  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
724  118827  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
738  120107  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
743  121832  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
732  123532  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
703  126250  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
718  130662  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
730  133755  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
747  134619  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
739  135460  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   
709  139755  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        150   

    learning_rate                                          max_depth  \
741   

In [126]:
df_analysis["hyperparams"] = df_analysis["hyperparams"].astype(object)

In [132]:
caca = df_analysis["hyperparams"].iloc[0]

In [137]:
df_analysis.head(5)

alpha                                        hyperparams  estimators  \
0   15193  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
1   16394  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
2   83183  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
3  109646  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
4  185450  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   

   learning_rate                                          max_depth  \
0           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
1           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
2           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
3           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
4           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   

   threshold        cost  learning_cost  train_auc  test_auc    final_cost  \
0       0.70  1988075.10   1.047961e+06   0.826748  0.821231  9.401146e+05   
1       0.70  1988075.10   1.130801e+06   0.826748  0.821231  8.572738e+05   
2       0.85  1987263.76   5.061557e+05   0.829214  0.823661  1.481108e+06   
3       0.85  1987263.76   6.671789e+05   0.829214  0.823661  1.320085e+06   
4       0.85  1987263.76   1.128435e+06   0.829214  0.823661  8.588292e+05   

   diff_auc  
0  0.005517  
1  0.005517  
2  0.005552  
3  0.005552  
4  0.005552

In [141]:
import re

max_depth_list = []
for caca in list(df_analysis["hyperparams"]):
    m = re.search('max_depth=(.+?)', caca)
    if m:
        max_depth_list.append(int(m.group(1)))

In [142]:
df_analysis["max_depth"] = max_depth_list

In [154]:
df_analysis

alpha                                        hyperparams  estimators  \
0    15193  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
1    16394  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
2    83183  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
3   109646  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
4   185450  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
5   108128  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
6    25348  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
7    31000  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
8   164985  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   
9    23406  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
10   31829  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
11   14789  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
12   22964  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         150   
13   11679  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
14   71990  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
15   42876  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
16   54744  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
17   56190  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
18   89873  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
19   87106  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
20   54330  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
21   49171  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
22  104294  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
23  126762  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
24   25051  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
25  149811  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
26   17139  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
27  158285  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
28   12408  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
29  127567  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   

    learning_rate  max_depth  threshold        cost  learning_cost  train_auc  \
0            0.01          6       0.70  1988075.10   1.047961e+06   0.826748   
1            0.01          6       0.70  1988075.10   1.130801e+06   0.826748   
2            0.01          6       0.85  1987263.76   5.061557e+05   0.829214   
3            0.01          6       0.85  1987263.76   6.671789e+05   0.829214   
4            0.01          6       0.85  1987263.76   1.128435e+06   0.829214   
5            0.01          6       0.85  1987263.76   6.579421e+05   0.829214   
6            0.01          6       0.85  1987263.76   1.542387e+05   0.829214   
7            0.01          6       0.85  1987263.76   1.886302e+05   0.829214   
8            0.01          6       0.85  1987263.76   1.003908e+06   0.829214   
9            0.01          6       0.85  1980368.94   7.571576e+05   0.829289   
10           0.01          6       0.85  1980368.94   1.029632e+06   0.829289   
11           0.01          6       0.85  1980368.94   4.784074e+05   0.829289   
12           0.01          6       0.85  1966387.00   1.076402e+06   0.829275   
13           0.01          6       0.80  1980286.78   1.833567e+05   0.828108   
14           0.01          6       0.80  1980286.78   1.130221e+06   0.828108   
15           0.01          6       0.80  1980286.78   6.731400e+05   0.828108   
16           0.01          6       0.80  1980286.78   8.594639e+05   0.828108   
17           0.01          6       0.80  1980286.78   8.821657e+05   0.828108   
18           0.01          8       0.90  1972517.68   6.450023e+05   0.832750 

In [23]:
df_analysis = df_collector[(df_collector["threshold"] ==0.2) &  (df_collector["final_cost"] > 0)]

In [30]:
df_analysis

alpha  estimators  learning_rate  max_depth  threshold  count_zero  \
1      37676          50           0.01          4        0.2       15306   
6      57030          50           0.01          4        0.2       15306   
11     81283          50           0.01          4        0.2       15306   
16     61622          50           0.01          4        0.2       15306   
21     54746          50           0.01          4        0.2       15306   
...      ...         ...            ...        ...        ...         ...   
5001   27348         200           0.01          4        0.2       14355   
5006  143943         200           0.01          4        0.2       14355   
5011   82172         200           0.01          4        0.2       14355   
5016  145278         200           0.01          4        0.2       14355   
5021   79390         200           0.01          4        0.2       14355   

      count_one        cost  learning_cost  train_auc  test_auc  final_cost  \
1         11694  1983300.38            0.0   0.826083  0.824467  1983300.38   
6         11694  1983300.38            0.0   0.826083  0.824467  1983300.38   
11        11694  1983300.38            0.0   0.826083  0.824467  1983300.38   
16        11694  1983300.38            0.0   0.826083  0.824467  1983300.38   
21        11694  1983300.38            0.0   0.826083  0.824467  1983300.38   
...         ...         ...            ...        ...       ...         ...   
5001      12645  1983300.38            0.0   0.828593  0.827221  1983300.38   
5006      12645  1983300.38            0.0   0.828593  0.827221  1983300.38   
5011      12645  1983300.38            0.0   0.828593  0.827221  1983300.38   
5016      12645  1983300.38            0.0   0.828593  0.827221  1983300.38   
5021      12645  1983300.38            0.0   0.828593  0.827221  1983300.38   

      diff_auc  
1     0.001617  
6     0.001617  
11    0.001617  
16    0.001617  
21    0.001617  
...        ...  
5001  0.001372  
5006  0.001372  
5011  0.001372  
5016  0.001372  
5021  0.001372  

[370 rows x 13 columns]

In [ ]:
df_analysis1 = pd.read_csv("")

In [31]:

import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
def plot_4d(df, col_cost):
    """ 
    Do 4d plot
    
    Args:
        - df (DataFrame Object): df to be represented.
        - col_cost (string): name of column that contains values in order to set colors
    """
    fig = go.Figure()
    fig.add_trace(go.Scatter3d(x=df.estimators, y=df.alpha, z=df.max_depth, name = "Cost", 
        mode='markers',
        marker=dict(
        size=6,
        color=df[col_cost],  # set color to an array/list of desired values
        colorscale='RdBu',   # choose a colorscale
        opacity=0.8), hovertemplate="estimators: %{x}<br>alpha: %{y} <br>max_depth: %{z}<extra></extra>")
    ),
                 

    
    #data = [data1]
    #fig = dict(data=data)
    fig.update_layout(
                        showlegend=False,scene = dict(
                    xaxis_title='Estimators',
                    yaxis_title='Alpha',
                    zaxis_title='max_depth of Base Learner',
                        ))
    iplot(fig)

In [26]:
del df_analysis["hyperparams"]

In [27]:
df_analysis.sort_values("final_cost")

alpha  estimators  learning_rate  max_depth  threshold  count_zero  \
4346   13241         150           0.01          6        0.2       17867   
3356   17215         120           0.01          6        0.2       17762   
2431   27776         100           0.01          6        0.2       17581   
661    12771          50           0.01          8        0.2       22056   
4266   11690         150           0.01          6        0.2       17867   
...      ...         ...            ...        ...        ...         ...   
1016  104574          75           0.01          4        0.2       14681   
1011   82538          75           0.01          4        0.2       14681   
1006   51980          75           0.01          4        0.2       14681   
1041  149556          75           0.01          4        0.2       14681   
5021   79390         200           0.01          4        0.2       14355   

      count_one        cost  learning_cost  train_auc  test_auc    final_cost  \
4346       9133  1917878.44   1.733839e+06   0.826280  0.824900  1.840399e+05   
3356       9238  1947011.80   1.683698e+06   0.826337  0.825059  2.633136e+05   
2431       9419  1931177.98   1.628399e+06   0.826514  0.825068  3.027788e+05   
661        4944  1939660.18   1.575866e+06   0.823704  0.813038  3.637945e+05   
4266       9133  1917878.44   1.530743e+06   0.826280  0.824900  3.871351e+05   
...         ...         ...            ...        ...       ...           ...   
1016      12319  1983300.38   0.000000e+00   0.827757  0.826482  1.983300e+06   
1011      12319  1983300.38   0.000000e+00   0.827757  0.826482  1.983300e+06   
1006      12319  1983300.38   0.000000e+00   0.827757  0.826482  1.983300e+06   
1041      12319  1983300.38   0.000000e+00   0.827757  0.826482  1.983300e+06   
5021      12645  1983300.38   0.000000e+00   0.828593  0.827221  1.983300e+06   

      diff_auc  
4346  0.001380  
3356  0.001278  
2431  0.001446  
661   0.010666  
4266  0.001380  
...        ...  
1016  0.001275  
1011  0.001275  
1006  0.001275  
1041  0.001275  
5021  0.001372  

[370 rows x 13 columns]

In [28]:
plot_4d(df_analysis[['alpha',  'estimators',  'max_depth', 'final_cost']], "final_cost")

In [32]:
plot_4d(df_analysis[['alpha',  'estimators',  'max_depth', 'diff_auc']], 'diff_auc')

In [65]:
ngb_clf = NGBClassifier(Base=DecisionTreeRegressor(ccp_alpha=0.0,
                                         criterion='friedman_mse', max_depth=6,
                                         max_features=None, max_leaf_nodes=None,
                                         min_impurity_decrease=0.0,
                                         min_impurity_split=None,
                                         min_samples_leaf=1,
                                         min_samples_split=2,
                                         min_weight_fraction_leaf=0.0,
                                         presort='deprecated',
                                         random_state=None, splitter='best'),
             col_sample=1.0,
              learning_rate=0.01, minibatch_frac=1.0, n_estimators=150,
              natural_gradient=True, tol=0.0001,
              verbose=True, verbose_eval=0)
ngb_clf.fit(X_train_resampled, y_train_resampled, sample_weight= get_sample_weights(y_train, y_train_resampled))

NGBClassifier(Base=DecisionTreeRegressor(ccp_alpha=0.0,
                                         criterion='friedman_mse', max_depth=6,
                                         max_features=None, max_leaf_nodes=None,
                                         min_impurity_decrease=0.0,
                                         min_impurity_split=None,
                                         min_samples_leaf=1,
                                         min_samples_split=2,
                                         min_weight_fraction_leaf=0.0,
                                         presort='deprecated',
                                         random_state=None, splitter='best'),
              Dist=<class 'ngboost.distns.categorical.k_categorical.<locals>.Categorical'>,
              Score=<class 'ngboost.scores.LogScore'>, col_sample=1.0,
              learning_rate=0.01, minibatch_frac=1.0, n_estimators=150,
              natural_gradient=True,
              random_state=RandomState(MT1

In [66]:
df_analysis.sort_values("final_cost").head(20)

alpha  estimators  learning_rate  max_depth  threshold  count_zero  \
4346   13241         150           0.01          6        0.2       17867   
3356   17215         120           0.01          6        0.2       17762   
2431   27776         100           0.01          6        0.2       17581   
661    12771          50           0.01          8        0.2       22056   
4266   11690         150           0.01          6        0.2       17867   
2361   26021         100           0.01          6        0.2       17581   
3406   14789         120           0.01          6        0.2       17762   
716    11213          50           0.01          8        0.2       22056   
631    10146          50           0.01          8        0.2       22056   
2261   20784         100           0.01          6        0.2       17581   
2456   15520         100           0.01          6        0.2       17581   
2256   15228         100           0.01          6        0.2       17581   
2376   14401         100           0.01          6        0.2       17581   
2426   14048         100           0.01          6        0.2       17581   
2406   10588         100           0.01          6        0.2       17581   
1461  160878          75           0.01          6        0.2       17381   
1411  157890          75           0.01          6        0.2       17381   
1391  146788          75           0.01          6        0.2       17381   
1316  143590          75           0.01          6        0.2       17381   
1421  143043          75           0.01          6        0.2       17381   

      count_one        cost  learning_cost  train_auc  test_auc    final_cost  \
4346       9133  1917878.44   1.733839e+06   0.826280  0.824900  1.840399e+05   
3356       9238  1947011.80   1.683698e+06   0.826337  0.825059  2.633136e+05   
2431       9419  1931177.98   1.628399e+06   0.826514  0.825068  3.027788e+05   
661        4944  1939660.18   1.575866e+06   0.823704  0.813038  3.637945e+05   
4266       9133  1917878.44   1.530743e+06   0.826280  0.824900  3.871351e+05   
2361       9419  1931177.98   1.525510e+06   0.826514  0.825068  4.056676e+05   
3406       9238  1947011.80   1.446425e+06   0.826337  0.825059  5.005864e+05   
716        4944  1939660.18   1.383618e+06   0.823704  0.813038  5.560425e+05   
631        4944  1939660.18   1.251956e+06   0.823704  0.813038  6.877039e+05   
2261       9419  1931177.98   1.218485e+06   0.826514  0.825068  7.126926e+05   
2456       9419  1931177.98   9.098774e+05   0.826514  0.825068  1.021301e+06   
2256       9419  1931177.98   8.927586e+05   0.826514  0.825068  1.038419e+06   
2376       9419  1931177.98   8.442748e+05   0.826514  0.825068  1.086903e+06   
2426       9419  1931177.98   8.235798e+05   0.826514  0.825068  1.107598e+06   
2406       9419  1931177.98   6.207334e+05   0.826514  0.825068  1.310445e+06   
1461       9619  1982169.70   1.735130e+05   0.824784  0.822259  1.808657e+06   
1411       9619  1982169.70   1.702903e+05   0.824784  0.822259  1.811879e+06   
1391       9619  1982169.70   1.583164e+05   0.824784  0.822259  1.823853e+06   
1316       9619  1982169.70   1.548672e+05   0.824784  0.822259  1.827302e+06   
1421       9619  1982169.70   1.542773e+05   0.824784  0.822259  1.827892e+06   

      diff_auc  
4346  0.001380  
3356  0.001278  
2431  0.001446  
661   0.010666  
4266  0.001380  
2361  0.001446  
3406  0.001278  
716   0.010666  
631   0.010666  
2261  0.001446  
2456  0.001446  
2256  0.001446  
2376  0.001446  
2426  0.001446  
2406  0.001446  
1461  0.002525  
1411  0.002525  
1391  0.002525  
1316  0.002525  
1421  0.002525

In [74]:
df_metric = pd.DataFrame(columns=  ["alpha", "threshold", 
                                       "cost",  "learning_cost"])
k = 0
for threshold in list(np.arange(0.2, 0.35, 0.05)):
    df_aux = pd.DataFrame(X_test, columns=cols_with_missing_indicators)
    df_aux['predicted'] = generate_y_pred_with_custom_threshold(ngb_clf, X_test, threshold)
    df_aux['proba_predicted'] = [proba[1] for proba in ngb_clf.predict_proba(X_test)]
    df_aux['real'] = list(y_test)
    df_aux['LoanPrincipal'] = df_aux.MonthlyIncome * 2
    for kix in range(0,1000):
        alpha = random.randint(10000, 30000)
        #alpha = random.randint(10000, 700000)
        df_collector.ix[str(k),'alpha'] = alpha
        df_collector.ix[str(k),'threshold'] = threshold
        print("k: "+str(k))
        print("alpha: "+str(alpha))
        print(threshold)
        print("cost "+str(cost_score(df_aux.LoanPrincipal, df_aux.predicted, df_aux.real)))
        print("learning cost "+str(calculate_learning_cost(df_aux.predicted,df_aux.proba_predicted, alpha)))
        print("th "+str(threshold))
        df_metric.ix[str(k),'cost'] = cost_score(df_aux.LoanPrincipal, df_aux.predicted, df_aux.real)
        df_metric.ix[str(k),'learning_cost'] = calculate_learning_cost(df_aux.predicted,df_aux.proba_predicted, alpha)
        k+=1
        print("sumando k")
        print("---------------------------------")

df_metric['final_cost'] = df_metric['cost'] - df_metric['learning_cost']
df_metric["%_inversion"] = (df_metric['final_cost']- df_metric['cost'])/(df_metric['cost'])

count_zero 937
count_one 26063
k: 0
alpha: 20536
0.2
cost 1947289.1999999927
learning cost 2770211.8750962713
th 0.2
sumando k
---------------------------------
k: 1
alpha: 13235
0.2
cost 1947289.1999999927
learning cost 1785340.5807800523
th 0.2
sumando k
---------------------------------
k: 2
alpha: 11544
0.2
cost 1947289.1999999927
learning cost 1557232.4642633079
th 0.2


KeyboardInterrupt: 

In [11]:
base0 = DecisionTreeRegressor(criterion="friedman_mse", max_depth=4)
base1 = DecisionTreeRegressor(criterion="friedman_mse", max_depth=6)
base2 = DecisionTreeRegressor(criterion="friedman_mse", max_depth=8)
base3 = DecisionTreeRegressor(criterion="friedman_mse", max_depth=12)

In [36]:
from utils import check_counts

In [42]:
#FIX MEEEEEEEEEEE: REFACTOR PLZZ !!!
df_collector = pd.DataFrame(columns=  ["alpha","hyperparams", "estimators", 
                                       "learning_rate", "max_depth", "threshold", "count_zero", "count_one",
                                       "cost", 
                                       "learning_cost",
                                       "train_auc", "test_auc"])
df_collector['hyperparams'] = df_collector['hyperparams'].astype('object')
k = 0
for estimator in [200,250,300]:
    for lr in [0.01]:
        for baset in [base0,base1,base2,base3]:
            ngb_clf = NGBClassifier(Dist=Bernoulli,
                                      verbose=True, Base=baset, n_estimators = estimator, 
                                    learning_rate = lr, verbose_eval = 0
                                     )
            print(ngb_clf)
            ngb_clf.fit(X_train_resampled, y_train_resampled, sample_weight= get_sample_weights(y_train, y_train_resampled))
            index_th = 0
            #en el primer iteraba el threashold desde 0.1 a 0.9 obviamente cuanto mas menor me daba peor.. entonces itero
            #solamente d esde 0.70 a 0.95
            for kix in range(0,2000):
                alpha = random.randint(10000, 80000)
                cost = cost_score(df_aux.LoanPrincipal, df_aux.predicted, df_aux.real)
                learning_cost = calculate_learning_cost(df_aux.predicted,df_aux.proba_predicted, alpha)
                if cost-learning_cost  > 0:
                    for threshold in list(np.arange(0.15, 0.4, 0.05)):
                        count_zero, count_one = check_counts(ngb_clf, X_test, threshold)
                        if (count_zero > 7000):
                            #alpha = random.randint(10000, 700000)
                            df_collector.ix[str(k),'alpha'] = alpha
                            df_collector.ix[str(k),'hyperparams'] = ngb_clf
                            df_collector.ix[str(k),'estimators'] = estimator
                            df_collector.ix[str(k),'learning_rate'] = lr
                            df_collector.ix[str(k),'max_depth'] = baset
                            threshold = round(threshold,2)
                            print("k: "+str(k))
                            df_aux = pd.DataFrame(X_test, columns=cols_with_missing_indicators)
                            df_aux['predicted'] = generate_y_pred_with_custom_threshold(ngb_clf, X_test, threshold)
                            df_aux['proba_predicted'] = [proba[1] for proba in ngb_clf.predict_proba(X_test)]
                            df_aux['real'] = list(y_test)
                            df_aux['LoanPrincipal'] = df_aux.MonthlyIncome * 2
                            print(threshold)
                            print("cost "+str(cost_score(df_aux.LoanPrincipal, df_aux.predicted, df_aux.real)))
                            print("th "+str(threshold))
                            df_collector.ix[str(k),'threshold'] = threshold
                            df_collector.ix[str(k),'count_zero'] = count_zero
                            df_collector.ix[str(k),'count_one'] = count_one
                            df_collector.ix[str(k),'cost'] = cost_score(df_aux.LoanPrincipal, df_aux.predicted, df_aux.real) #predicted tomo threshold (p(x|y=0))
                            df_collector.ix[str(k),'learning_cost'] = calculate_learning_cost(df_aux.predicted,df_aux.proba_predicted, alpha) #predicted tomo threshold (p(x|y=0)), probas predichas por el modelo para y = 1 y alpha
                            # predict probabilities
                            train_probs = ngb_clf.predict_proba(X_train)
                            test_probs = ngb_clf.predict_proba(X_test)
                            # keep probabilities for the positive outcome only
                            train_probs = train_probs[:, 1]
                            test_probs = test_probs[:, 1]
                            # calculate scores
                            train_auc = roc_auc_score(y_train, train_probs)
                            test_auc = roc_auc_score(y_test, test_probs)
                            df_collector.ix[str(k),'train_auc'] = train_auc
                            df_collector.ix[str(k),'test_auc'] = test_auc
                            k+=1
                            print("sumando k")
                            print("---------------------------------")
            del ngb_clf
df_collector['final_cost'] = df_collector['cost'] - df_collector['learning_cost']

NGBClassifier(Base=DecisionTreeRegressor(ccp_alpha=0.0,
                                         criterion='friedman_mse', max_depth=4,
                                         max_features=None, max_leaf_nodes=None,
                                         min_impurity_decrease=0.0,
                                         min_impurity_split=None,
                                         min_samples_leaf=1,
                                         min_samples_split=2,
                                         min_weight_fraction_leaf=0.0,
                                         presort='deprecated',
                                         random_state=None, splitter='best'),
              Dist=<class 'ngboost.distns.categorical.k_categorical.<locals>.Categorical'>,
              Score=<class 'ngboost.scores.LogScore'>, col_sample=1.0,
              learning_rate=0.01, minibatch_frac=1.0, n_estimators=200,
              natural_gradient=True,
              random_state=RandomState(MT1

KeyboardInterrupt: 

In [43]:
df_collector

Empty DataFrame
Columns: [alpha, hyperparams, estimators, learning_rate, max_depth, threshold, count_zero, count_one, cost, learning_cost, train_auc, test_auc]
Index: []

In [32]:
df_collector['diff_auc'] = df_collector['train_auc'] - df_collector['test_auc']


In [34]:
df_collector[(df_collector["final_cost"] > 0) & (df_collector["learning_cost"] > 0)].sort_values("final_cost")

alpha                                        hyperparams estimators  \
260   46401  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        200   
2285  28494  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        300   
2445  26021  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        300   
491   10376  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        200   
350   37829  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        200   
1480  24584  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        250   
1265  23640  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        250   
315   34191  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        200   
1410  22494  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        250   
2345  20784  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        300   
1445  21777  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        250   
1460  21685  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        250   
255   32550  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        200   
1285  21508  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        250   
2290  19887  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        300   
1470  18134  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        250   
2340  15228  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        300   
2460  14401  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        300   
380   21417  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        200   
375   18406  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        200   
2490  10588  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        300   
480   15548  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        200   
295   12076  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        200   
490   10376  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...        200   

     learning_rate                                          max_depth  \
260           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
2285          0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
2445          0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
491           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
350           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
1480          0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
1265          0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
315           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
1410          0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
2345          0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
1445          0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
1460          0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
255           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
1285          0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
2290          0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
1470          0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
2340          0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
2460          0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
380           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
375           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
2490          0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
480           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
295           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   
490           0.01  DecisionTreeRegressor(ccp_alpha=0.0, criterion...   

     threshold count_zero count_one         cost learning_cost train_auc  \
260       0.15      20999      6001  1.95362e+06   1.95081e+06  0.830175   
2285      0.15      21011      5989  1.97044e+06   1.95445e+06  0.829978   
2445      0.15      21011 

In [ ]:
ngb_clf = 

In [35]:
df_test = pd.read_csv("results_2exp_1rstpart.csv")

In [36]:
df_test.rename(columns={'count_zero':'count_one_', 'count_one':'count_zero_'}, inplace=True)

In [37]:
df_test[(df_test["final_cost"] > 0)].sort_values(["final_cost", "diff_auc"]).head(20)

alpha                                        hyperparams  estimators  \
4260   83336  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         150   
4255   82833  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         150   
1497   16650  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
448    27849  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
4460   80217  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         150   
4275   79155  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         150   
3295  179570  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
4360   77963  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         150   
4346   13241  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         150   
4485   75814  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         150   
3310  171864  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
3365  169838  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
3495  168715  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
3300  168355  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
3356   17215  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
3330  166433  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
3265  165628  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
3375  164965  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         120   
1447   14649  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          75   
2431   27776  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         100   

      learning_rate  max_depth  threshold  count_one_  count_zero_  \
4260           0.01          6       0.15       21045         5955   
4255           0.01          6       0.15       21045         5955   
1497           0.01          6       0.25       14925        12075   
448            0.01          6       0.30       13520        13480   
4460           0.01          6       0.15       21045         5955   
4275           0.01          6       0.15       21045         5955   
3295           0.01          6       0.15       21046         5954   
4360           0.01          6       0.15       21045         5955   
4346           0.01          6       0.20       17867         9133   
4485           0.01          6       0.15       21045         5955   
3310           0.01          6       0.15       21046         5954   
3365           0.01          6       0.15       21046         5954   
3495           0.01          6       0.15       21046         5954   
3300           0.01          6       0.15       21046         5954   
3356           0.01          6       0.20       17762         9238   
3330           0.01          6       0.15       21046         5954   
3265           0.01          6       0.15       21046         5954   
3375           0.01          6       0.15       21046         5954   
1447           0.01          6       0.25       14925        12075   
2431           0.01          6       0.20       17581         9419   

            cost  learning_cost  train_auc  test_auc     final_cost  diff_auc  
4260  1960561.36   1.942076e+06   0.826280  0.824900   18485.543026  0.001380  
4255  1960561.36   1.930354e+06   0.826280  0.824900   30207.537553  0.001380  
1497  1915569.22   1.852691e+06   0.824784  0.822259   62878.152299  0.002525  
448   1967078.18   1.885824e+06   0.822885  0.820535   81254.503628  0.002349  
4460  1960561.36   1.869390e+06   0.826280  0.824900   91171.230762  0.001380  
4275  1960561.36   1.844641e+06   0.826280  0.824900  115920.253005  0.001380  
3295  1960961.02   1.827497e+06   0.826337  0.825059  133464.230286  0.001278  
4360  1960561.36   1.816863e+06   0.826280  0.824900  143698.816577  0.001380  
4346  1917878.44   1.733839e+06   0.826280  0.824900  184039.864054  0.001380  
4485  1960561.36   1.766782e+06   0.826280  0.824900  193779.465164  0.00138

In [49]:
ngb_clf = NGBClassifier(Base=DecisionTreeRegressor(ccp_alpha=0.0,
                                         criterion='friedman_mse', max_depth=6,
                                         max_features=None, max_leaf_nodes=None,
                                         min_impurity_decrease=0.0,
                                         min_impurity_split=None,
                                         min_samples_leaf=1,
                                         min_samples_split=2,
                                         min_weight_fraction_leaf=0.0,
                                         presort='deprecated',
                                         random_state=None, splitter='best'),
             col_sample=1.0,
              learning_rate=0.01, minibatch_frac=1.0, n_estimators=150,
              natural_gradient=True, tol=0.0001,
              verbose=True, verbose_eval=0)
ngb_clf.fit(X_train_resampled, y_train_resampled, sample_weight= get_sample_weights(y_train, y_train_resampled))

NGBClassifier(Base=DecisionTreeRegressor(ccp_alpha=0.0,
                                         criterion='friedman_mse', max_depth=6,
                                         max_features=None, max_leaf_nodes=None,
                                         min_impurity_decrease=0.0,
                                         min_impurity_split=None,
                                         min_samples_leaf=1,
                                         min_samples_split=2,
                                         min_weight_fraction_leaf=0.0,
                                         presort='deprecated',
                                         random_state=None, splitter='best'),
              Dist=<class 'ngboost.distns.categorical.k_categorical.<locals>.Categorical'>,
              Score=<class 'ngboost.scores.LogScore'>, col_sample=1.0,
              learning_rate=0.01, minibatch_frac=1.0, n_estimators=150,
              natural_gradient=True,
              random_state=RandomState(MT1

In [51]:
df_aux = pd.DataFrame(X_test, columns=cols_with_missing_indicators)
df_aux['predicted'] = generate_y_pred_with_custom_threshold(ngb_clf, X_test, 0.2)
df_aux['real'] = list(y_test)
df_aux['LoanPrincipal'] = df_aux.MonthlyIncome * 2
#cost_score(df_aux.LoanPrincipal, df_aux.predicted, df_aux.real)

count_zero 937
count_one 26063


In [52]:
count_zero, count_one = check_counts(ngb_clf, X_test, 0.2)

In [53]:
count_zero

18148

In [54]:
count_one

8852

In [4]:
df_anal1 = pd.read_csv("metrics_2nd_exp.csv")

In [5]:
df_anal2 = pd.read_csv("metrics_2exp_2nd_part.csv")

In [7]:
df_anal1

alpha  threshold        cost  learning_cost    final_cost  %_inversion
0     57739       0.15  1964824.44   4.218270e+05  1.542997e+06     0.214689
1     28496       0.15  1964824.44   2.081848e+05  1.756640e+06     0.105956
2     27779       0.15  1964824.44   2.029466e+05  1.761878e+06     0.103290
3     47810       0.15  1964824.44   3.492882e+05  1.615536e+06     0.177771
4     12678       0.15  1964824.44   9.262237e+04  1.872202e+06     0.047140
...     ...        ...         ...            ...           ...          ...
1039  10927       0.20  1947289.20   1.474002e+06  4.732872e+05     0.756951
1040  11336       0.20  1947289.20   1.529174e+06  4.181150e+05     0.785284
1041  10196       0.20  1947289.20   1.375393e+06  5.718957e+05     0.706312
1042  12303       0.20  1947289.20   1.659618e+06  2.876711e+05     0.852271
1043  12786       0.20  1947289.20   1.724773e+06  2.225167e+05     0.885730

[1044 rows x 6 columns]

In [8]:
df_anal2

alpha  threshold       cost  learning_cost    final_cost  %_inversion
0     4573        0.2  1947289.2   6.168767e+05  1.330413e+06    -0.316787
1     3462        0.2  1947289.2   4.670079e+05  1.480281e+06    -0.239825
2     9661        0.2  1947289.2   1.303224e+06  6.440648e+05    -0.669251
3     6438        0.2  1947289.2   8.684566e+05  1.078833e+06    -0.445982
4     8925        0.2  1947289.2   1.203941e+06  7.433478e+05    -0.618265
..     ...        ...        ...            ...           ...          ...
995   4246        0.2  1947289.2   5.727659e+05  1.374523e+06    -0.294135
996   6145        0.2  1947289.2   8.289322e+05  1.118357e+06    -0.425685
997   4855        0.2  1947289.2   6.549172e+05  1.292372e+06    -0.336322
998   6619        0.2  1947289.2   8.928726e+05  1.054417e+06    -0.458521
999   9024        0.2  1947289.2   1.217296e+06  7.299931e+05    -0.625123

[1000 rows x 6 columns]

In [6]:
df1 = pd.read_csv("results_2exp_1rstpart.csv")

In [9]:
df1

alpha                                        hyperparams  estimators  \
0      37676  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
1      37676  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
2      37676  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
3      37676  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
4      37676  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...          50   
...      ...                                                ...         ...   
5019  145278  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         200   
5020   79390  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         200   
5021   79390  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         200   
5022   79390  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         200   
5023   79390  NGBClassifier(Base=DecisionTreeRegressor(ccp_a...         200   

      learning_rate  max_depth  threshold  count_zero  count_one        cost  \
0              0.01          4       0.15       24158       2842  1983300.38   
1              0.01          4       0.20       15306      11694  1983300.38   
2              0.01          4       0.25       13638      13362  1983300.38   
3              0.01          4       0.30       12464      14536  1983300.38   
4              0.01          4       0.35       11273      15727  1983300.38   
...             ...        ...        ...         ...        ...         ...   
5019           0.01          4       0.35        9985      17015  1983300.38   
5020           0.01          4       0.15       16945      10055  1983300.38   
5021           0.01          4       0.20       14355      12645  1983300.38   
5022           0.01          4       0.25       12872      14128  1983300.38   
5023           0.01          4       0.30       11337      15663  1983300.38   

      learning_cost  train_auc  test_auc  final_cost  diff_auc  
0               0.0   0.826083  0.824467  1983300.38  0.001617  
1               0.0   0.826083  0.824467  1983300.38  0.001617  
2               0.0   0.826083  0.824467  1983300.38  0.001617  
3               0.0   0.826083  0.824467  1983300.38  0.001617  
4               0.0   0.826083  0.824467  1983300.38  0.001617  
...             ...        ...       ...         ...       ...  
5019            0.0   0.828593  0.827221  1983300.38  0.001372  
5020            0.0   0.828593  0.827221  1983300.38  0.001372  
5021            0.0   0.828593  0.827221  1983300.38  0.001372  
5022            0.0   0.828593  0.827221  1983300.38  0.001372  
5023            NaN        NaN       NaN         NaN       NaN  

[5024 rows x 14 columns]